In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import os
import random
import operator
import pandas as pd
import numpy as np
from sklearn.metrics import mean_absolute_error as MAE
from sklearn.metrics import mean_squared_error as MSE
import pandasql as sqldf

Ziel dieses Notebooks ist es Klassen bereit zu stellen, welche anhand einer Grid und Random Search orientierten Methode die Hyperparameter eines Neuronalen Netzes optimieren, vielversprechende Neuronale Netze mit Hilfe einer Crossvalidation gegeneinander zu testen und schließlich das beste Modell auf allen vorliegenden Daten zu trainieren (ausgenommen dem letzten Rennen der Rennsaison 2017) und dieses Modell schließlich als Teil des finalen Testens auf diesem letzten Rennen zu testen.<br>Da die Berechnungen sehr zeitaufwendig sind (Zeitangaben sind an Google Colab Rechenzeit orientiert), wird zuletzt eine Möglichkeit bereitgestellt, das so wie zuvor beschriebene, vortrainierte Netz in das Notebook zu laden und die Vorhersage auf dem letzten Rennen mit Hilfe dieses Modells zu machen.  

In der ersten Klasse werden die Hyperparameter Layeranzahl, Aktivierungsfunktionen und Neuronenanzahl betrachtet; die Neuronenanzahl ist Teil einer Random Search, die Layeranzahl einer Grid Search und die Aktivierungsfunktionen werden mit einer Mischung dieser beiden Methoden gesucht. Die zweite Klasse optimiert die Anzahl von Trainingsepochen und die Lernrate für den Adam Optimizer mit Hilfe einer Grid Search orientierten Methode.

Für die Optimierung wird zusätzlich eine Klasse benötigt, welche dynamisch Neuronale Netze erzeugt.

## Laden der Daten:
Mit Hilfe von hier bereitgestellten Methoden werden Daten aus dem Ordner sliced_data geladen und vorbereitet. Zur Vorbereitung zählt das Aufteilen in train, dev, test Trainingssätze und das Umwandeln dieser in Tensoren.

In [ ]:
def load_data(directory = 'sliced_data'):
    '''
        Funktion, die die aufbereiteten/vorbereiteten Daten aus existierenden CSV Dateien 
        einliest und je nach Vollständigkeit in zwei Dictionaries abspeichert,
        geschlüsselt nach der jeweiligen RaceId
    '''
    if os.path.exists(directory):
        csv_filenames = []
        #auslesen aller csv file dateinamen aus formula 1 datensatz und abspeichern in liste
        for filename in os.listdir(os.getcwd()+'/'+directory):
            typ = filename.split('.')[-1]
            name = filename.split('.')[0]
            if typ == 'csv':
                csv_filenames.append(filename)
        sliced_races = {}
        #einlesen und abspeichern als dataframe aller dateien
        for file in csv_filenames:
            try:
                df = pd.read_csv(directory+'/'+file, engine = 'python', sep = ';', decimal = '.')
                del df['Unnamed: 0']
            except Exception as e:
                df = pd.read_csv(directory+'/'+file, engine = 'c', sep = ';', decimal = '.')
                del df['Unnamed: 0']
                print(e)
            f = int(file.split('_')[-1].split('.')[0]) #raceid wird als key gesetzt
            sliced_races[f] = df
        print('Einlesen der '+directory+' Dateien erfolgreich')
    else:
        raise ('sliced Dateien können nicht eingelesen werden, da kein entsprechendes Verzeichnis existiert!')
   
    return sliced_races

def train_dev_test(data_dict, train_p = 0.7, dev_p = 0.2, test_p = 0.1, nogo_columns = []):
    
    if round(train_p+dev_p+test_p,1) !=1.0:
        raise ValueError ('No valid train/dev/test distribution')
    
    '''
        Daten werde in einem Dictionary übergeben, Dataframes werden in dieser 
        Funktion geshuffled und dann in einen Traindatensatz, einen Development-
        datensatz und in einen Testdatensatz aufgeteilt.
    '''
    #aufteilen in train, dev, test counter
    train_count = round(len(data_dict.keys())*train_p, 0)
    dev_count = train_count+round(len(data_dict.keys())*dev_p,0)
    test_count = len(data_dict.keys())-(train_count+dev_count)
    
    #shufflen der übergebenen Daten
    keys = list(data_dict.keys())
    random.shuffle(keys)
    data_shuffled = {}
    for key in keys:
        data_shuffled[key] = data_dict[key]
        
    #erzeugen separater train,dev,test dictionaries
    train = {}
    dev = {}
    test = {}
    c = 0
    
    for id, df in data_shuffled.items():
        #entfernen nicht gewollter spalten aus dataframe
        cols = [col for col in df.columns if col not in nogo_columns]
        df = df[cols]
        if c < train_count:
            train[id] = df
        elif c >= train_count and c < dev_count:
            dev[id] = df
        else:
            test[id] = df
        c += 1
                
    return train, dev, test

def to_tensor(train_data, dev_data, test_data, nogo_columns = []):
    '''
        Funktion erhält zuvor erzeugte train, dev und test Dictionarys mit Formel 1 Rennen
        und wandelt die DateFrames in Tensoren um. Den Tensoren wird jeweils ihr Target Value
        (podium_podition) zugeordnet. In Dictionary Form werden die Tensoren zurück gegeben.
        Nicht gewollte Spalten (in nogo_columns) werden entfernt.
    '''
    train = []
    train_ = {}
    dev = []
    dev_ = {}
    test = []
    test_ = {}
    
    for id, race in train_data.items():
        for did in race.driverId.unique():
            temp = race.where(race.driverId == did).dropna(how = "all")
            temp_y = list(temp["podium_position"])
            #nicht gewollte Attribute werden aus Datensatz entfernt (bspw. podium_position)
            cols = [col for col in temp.columns if col not in nogo_columns]
            temp_x = temp[cols]
            #die letze runde eines Fahrers wird betrachtet (enthält kumulierte Informationen über zuvor gefahrene Runden)
            temp_x = temp_x.tail(1)
            x_tensor = torch.tensor(temp_x[cols].values)
            train.append((x_tensor, [temp_y[0]]))#speichern von tensor und target als tupel
        train_[id] = train
        train = []
    if len(list(dev_data.keys())) != 0:#wird nur bei train/dev/test benötigt nicht bei train/test
        for id, race in dev_data.items():
            for did in race.driverId.unique():
                temp = race.where(race.driverId == did).dropna(how = "all")
                temp_y = list(temp["podium_position"])
                cols = [col for col in temp.columns if col not in nogo_columns]
                temp_x = temp[cols]
                temp_x = temp_x.tail(1)
                x_tensor = torch.tensor(temp_x[temp_x.columns].values)
                dev.append((x_tensor, [temp_y[0]]))
            dev_[id] = dev
            dev = []
    if len(list(test_data.keys()))!=0:
        for id, race in test_data.items():
            for did in race.driverId.unique():
                temp = race.where(race.driverId == did).dropna(how = "all")
                temp_y = list(temp["podium_position"])
                cols = [col for col in temp.columns if col not in nogo_columns]
                temp_x = temp[cols]
                temp_x = temp_x.tail(1)
                x_tensor = torch.tensor(temp_x[temp_x.columns].values)
                test.append((x_tensor, [temp_y[0]]))
            test_[id] = test
            test = []
        
    return train_,dev_,test_

Einlesen der Dateien als Dataframes, welche in zwei Dictionaries gespeichert werden:<br>
- Attribut directory verweißt auf den Ordnernamen der sliced Dateien, Default ist 'sliced_data'
- Rennen sind standardmäßig nach 50% gesliced (siehe hierzu Datenaufbereitung)

<br> Einmal für das ganze Notebook wird festgelegt, ob Cuda beim Training der Neuronalen Netze verwendet werden soll:

**Version wenn Notebook nicht in Google Colab verwendet wird:**

In [ ]:
cuda = input('Cuda? [y/n]: ')
sliced_races = load_data(directory = 'sliced_data')

Cuda? [y/n]: y


**Version wenn Notebook in Google Colab ausgeführt wird:**
<br> Wenn diese Alterntive gewählt wird sollten die CSV Dateien aus dem Ordner sliced_data ausgewählt und komplett hochgeladen werden.

In [ ]:
from google.colab import files
cuda = input('Cuda? [y/n]: ')
uploaded = files.upload()

sliced_races = {}
for element in uploaded:
    try:
                df = pd.read_csv(element, engine = 'python', sep = ';', decimal = '.')
                del df['Unnamed: 0']
    except Exception as e:
                df = pd.readcsv(element, engine = 'c', sep = ';', decimal = '.')
                del df['Unnamed: 0']
                print(e)
    f = int(element.split('_')[-1].split('.')[0]) #raceid wird als key gesetzt
    sliced_races[f] = df

Saving sliced_841.csv to sliced_841.csv
Saving sliced_842.csv to sliced_842.csv
Saving sliced_843.csv to sliced_843.csv
Saving sliced_844.csv to sliced_844.csv
Saving sliced_845.csv to sliced_845.csv
Saving sliced_846.csv to sliced_846.csv
Saving sliced_847.csv to sliced_847.csv
Saving sliced_848.csv to sliced_848.csv
Saving sliced_849.csv to sliced_849.csv
Saving sliced_850.csv to sliced_850.csv
Saving sliced_851.csv to sliced_851.csv
Saving sliced_852.csv to sliced_852.csv
Saving sliced_853.csv to sliced_853.csv
Saving sliced_854.csv to sliced_854.csv
Saving sliced_855.csv to sliced_855.csv
Saving sliced_856.csv to sliced_856.csv
Saving sliced_857.csv to sliced_857.csv
Saving sliced_858.csv to sliced_858.csv
Saving sliced_859.csv to sliced_859.csv
Saving sliced_860.csv to sliced_860.csv
Saving sliced_861.csv to sliced_861.csv
Saving sliced_862.csv to sliced_862.csv
Saving sliced_863.csv to sliced_863.csv
Saving sliced_864.csv to sliced_864.csv
Saving sliced_865.csv to sliced_865.csv


Aufteilen des Datensatzes in einen Trainings-, einen Development- und einen Testteil mit Hilfe der Funktion train_dev_test(). Standardmäßig wird der Datensatz zu 70% in Trainings-, zu 20% in Dev- und zu 10% in Testdaten aufgeteilt. Die Verteilung kann mit den Parametern train_p,dev_p,test_p die der Funktion train_dev_test() übergeben werden können, angepasst werden. Wichtig ist bloß, dass insgesamt train_p,dev_p und test_p 1 ergeben. Die Datenbeispiele aus sliced_races werden vor dem Aufteilen geshuffled. Die Funktion train_dev_test() gibt die Datenbeispiele dann wieder in Dictionary Form zurück, wobei jeder RaceId ein DataFrame mit Renndaten zugeordnet wird. Im nächsten Schritt werden die drei Datensammlungen der Funktion to_tensor() übergeben, die nicht gewünschte Spalten aus den Datensätzen entfernt (nogo_columns) und diese dann in Tensoren abspeichert, die wiederrum  ihrem Targetvalue (podiums_position) zugeordnet werden, um die Überprüfung der Vorhersagen später zu vereinfachen. Tupel mit Datensatz und Targetvalue werden dann wieder in dem jeweiligen Dictionary abgespeichert und ihrer RaceId zugeordnet.

In [ ]:
#definieren nicht gewollter Attribute (Attribute die nicht dem Modell übergeben werden sollen):
nogo_columns = ['year', 
                'podium_position', 
                'raceId',
                'lap_number',
                'driverId', 
                'driver_fullname',
                'total_milliseconds',
               'lap_in_milliseconds',
               'total_minutes'
                ]
#train dev test splitting
train, dev, test = train_dev_test(sliced_races)
#umwandeln in Tensoren und entfernen der nogo_columns
train_T, dev_T, test_T = to_tensor(train, dev, test, nogo_columns)

print('Train:',len(train))
print('Dev:',len(dev))
print('Test:',len(test))
print('Rennen insgesamt:', len(train)+len(dev)+len(test))
print(25*'=')
print('Tensoren:')
print('Train:',len(train_T))
print('Dev:',len(dev_T))
print('Test:',len(test_T))
print('Rennen insgesamt:', len(train_T)+len(dev_T)+len(test_T))

Train: 96
Dev: 27
Test: 14
Rennen insgesamt: 137
Tensoren:
Train: 96
Dev: 27
Test: 14
Rennen insgesamt: 137


## Hyperparameteroptimierung des Neuronalen Netzes:
#### Definieren von notwendigen Klassen: 
    
Zuerst werden zwei Klassen für Neuronale Netze definiert. Die erste Klasse definiert ein statisches Neuronales Netz, von dem wir wissen, dass es auf unseren Daten gut funktioniert. Die zweite Klasse definiert ein Dynamisches Neuronales Netz, welches in der Hyperparamteroptimierung verwendet wird, um Netze zu erzeugen, die gegen das statische Netz getestet werden.
Der dynamischen Klasse werden Dictionarys übergeben, die spezifizieren wie das Neuronale Netz erzeugt werden soll. Ein Beispiel kann wie folgt aussehen:<br>

{
                 'first'    :    ['linear', 10,150],<br>
                 'relu0'    :    ['linear',150,180],<br>
                 'relu1'    :    ['dropout',0,0],<br>
                 'no_activation0'    :    ['linear',180,190],<br>
                 'relu2'    :    ['linear',190,120],<br>
                 'relu3'    :    ['linear',120,100],<br>
                 'relu4'    :    ['linear',100,70],<br>
                 'relu5'    :    ['linear',70,30],<br>
                 'relu6'    :    ['linear',30,1]
}<br>
         
Dieses Dictionary würde ein Netz erzeugen, wie es in der statischen Klasse definiert wird. Die Keys des Dictionarys geben die dem Layer vorhergehende Activationfunction an (keine für das erste Layer, aus diesem Grund das Stichwort first), während der zugeordnete Value eine Liste mit Layerspezifikationen enthält. An erster Stelle wird der Typ des Layers definiert (dropout oder linear), an zweiter Stelle die Anzahl der Input Neuronen und an dritter Stelle die Anzahl der Output Neuronen für das Layer.

Die nächsten Klassen werden für die Hyperparameteroptimierung definiert. In der ersten Klasse werden dynamisch Neuronale Netze erzeugt, die mit unterschiedlichen Layeranzahlen und Neuronenanzahlen erzeugt werden. Von jeder Layeranzahl wird eine Variation verschiedener Netze erzeugt, sodass eine feste Anzahl Netze mit einer festen Layeranzahl gegen Netz mit einer anderen Anzahl von Layern getestet werden kann. <br>
In der zweiten Klasse werden die Parameter Trainigsepochen und Lernrate für den Adam OPtimizer optimiert. Die Klasse erhält das statische Neuronale Netz und das beste der dynamisch erzeugten Neuronalen Netze und optimiert diese Parameter für beide Netze.

In [8]:
class Netz(nn.Module):
    def __init__(self):
        super(Netz,self).__init__()
        self.fc1 = nn.Linear(52, 150)
        self.fc2 = nn.Linear(150, 180)
        self.fc3 = nn.Linear(180, 190)
        self.fc4 = nn.Linear(190, 120)
        self.fc5 = nn.Linear(120, 100)
        self.fc6 = nn.Linear(100, 70)
        self.fc7 = nn.Linear(70, 30)
        self.fc8 = nn.Linear(30, 1)
        self.dropout = nn.Dropout()
        
        
    def forward(self,x):
        x = self.fc1(x.float())
        x = F.relu(x.float())
        x = self.fc2(x.float())
        x = F.relu(x.float())
        x = self.dropout(x)
        x = self.fc3(x.float())
        x = F.relu(x.float())
        x = self.fc4(x.float())
        x = F.relu(x.float())
        x = self.fc5(x.float())
        x = F.relu(x.float())
        x = self.fc6(x.float())
        x = F.relu(x.float())
        x = self.fc7(x.float())
        x = F.relu(x.float())
        x = self.fc8(x.float())
        return x

class NetzDynamic(nn.Module):
    
    def __init__(self, layer_information):
        super(NetzDynamic,self).__init__()
        self.__layer_information = layer_information
        #definieren von einer Moduleliste, die alle Layer des Netzes enthalten wird
        self.layers = nn.ModuleList()
        
        #erzeugen der in layer_information übergebeben Layer und hinzufügen zu layers Moduleliste
        for specs in self.__layer_information.values():
            type_ = specs[0]
            in_ = specs[1]
            out_ = specs[2]
            if type_ == 'linear':
                self.layers.append(nn.Linear(in_,out_))
            if type_ == 'dropout':
                self.layers.append(nn.Dropout())
        
    def forward(self, x):
        #definieren eines dynamischen forward pass, activation function richtet sich nach dictionary key
        lay_idx = 0
        for activation, specs in self.__layer_information.items():
            if activation.startswith('relu'):
                layer = self.layers[lay_idx] #auswählen des relevanten Layers aus layers ModuleList
                if specs[0] == 'dropout':
                    x = F.relu(x.float())#anwenden der activation function
                    x = layer(x)
                else:
                    x = F.relu(x.float())
                    x = layer(x.float()) 
            if activation.startswith('sigmoid'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = torch.sigmoid(x.float())
                    x = layer(x)
                else:
                    x = torch.sigmoid(x.float())
                    x = layer(x.float())
                    
            if activation.startswith('tanh'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = torch.tanh(x.float())
                    x = layer(x)
                else:
                    x = torch.tanh(x.float())
                    x = layer(x.float())
            if activation.startswith("first"):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float())
            if activation.startswith("no_activation"):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float()) 
            lay_idx += 1#updaten der layerid, um forward pass ins nächste layer zu machen
        
        return x

In [ ]:
class HP_Layer_Optimizer(object):
    
    def __init__ (self, 
                  layer_range = (2,8), #range mindestanzahl layer, max anzahl layer
                  input_start = 52, #anzahl inputneuronen für das Inputlayer
                  output_last = 1, #anzahl outputneuronen für das letzte layer
                  in_out_range = (30,200), #range in der sich die anzahl der Neuronen für die Hiddenlayer bewegen soll
                  random_activation = False,#boolean, die angibt ob activation functions random gepicked werden sollen
                  types = ['linear', 'dropout'],#layertypen, von denen gewählt wird
                  activations = ['relu', 'sigmoid', 'tanh'],#activation functions
                  activation_dist = [0.5,0.25,0.25],#wenn random_activation == False wird hier die Häufigkeit für jede Activation übergeben, nicht implementiert
                  dropout_num = 1,#anzahl von dropoutlayern pro NN
                  cuda = True,#soll mit cuda gearbeitet werden?
                  lr = 0.0001,#lernrate für adam optimizer
                  max_epochs = 5,#anzahl der Trainingsepochen
                  create_combinations = True, #sollen von der Klasse Netze erzeugt werden, oder sollen diese von außen in die Klasse gegeben werden?
                  create_variations = False,#soll von jeder Layeranzahl mehr als ein Netz erzeugt werden?
                  num_variations = 4, #wenn Variationen erzeugt werden sollen wird eine festgelegte Zahl Netze mit 4 Layer, eine festgelegte Anzahl mit 5 Layern usw. erzeugt
                  pure_activations = True #wenn random_activation auf True gesetzt ist kann hier festgelegt werden, dass zusätzlich zu absolut zufällig kombinierten activationfunctions
                  #auch noch Netze erzeugt werden, die nur einheitliche activation functions haben (pure sind)
                  ):
        
        self.__model = None #model, welches trainiert und getestet wird, wird hier zwischengespeichert
        self.__layer_range = layer_range #min und max anzahl von layern in Tupelform
        self.__input_start = input_start#Inputgröße für Startlayer/Inputlayer
        self.__output_last = output_last#Outputgröße für letztes Layer / Outputlayer
        self.__in_out_range = in_out_range#range in der sich die Anzahl der In- und Outputs für die Hiddenlayer bewegen soll (Tupelform)
        self.__layer_types = types#liste welche Layertypen enthält (bspw. linear oder dropout)
        self.__dropout_number = dropout_num#anzahl von layern, die pro Netz ein dropout Layer sein sollen
        self.__random_activation = random_activation#Boolean, ob die activation zufällig gewählt werden soll
        self.__create_variations = create_variations
        self.__number_of_variations = num_variations
        self.__pure = pure_activations
        
        self.__combination_results = {}#dictionary, die dem schlüssel zu einer NN Kombi einen MAE zuordnet
        self.model_specs_combinations = {}#dictionary, welches die jeweiligen NN Kombinationen enthält (einem Schlüssel zugeordnet)
        self.train_data = None#trainingsdaten, die dem Optimizer übergeben werden für die Modelle
        self.test_data = None#developmentdaten, um die Modelle zu testen und Aussagen über die besten Kombinationen zu treffen
        self.lr = lr#lernrate für Modell OPtimizer (default Adam)
        self.max_epochs = max_epochs#Anzahl der Trainingsepochen
        self.cuda = cuda#Boolean, ob mit cuda gearbeitet werden soll oder nicht
        self.opt_combination = {}#dictionary enthält optimale kombination aus möglichen kombinationen
        
        self.__activations = None#entweder Liste (wenn activations random ausgewählt werden sollen), oder dictionary, 
        #wenn activation functions mit einer bestimmten Häufigkeit verwendet werden sollen
        if self.__random_activation:#random pick von activation functions
            self.__activations = activations
        else:#activation function sollen mit einer gewissen häufigkeit ausgewählt werden
            k = {}
            for a in range(len(types)):#zuordnen einer häufihkeit aus activation_dist liste zu jeder activation function aus types
                act = types[a]
                dist = activation_dist[a]
                k[act] = dist
            self.__activations = k
            
        #aufrufen der Funktion, die anhand der übergebenen Parameter Modellkombinationen erzeugt
        if create_combinations:
            print("in constructor bevor die kombinationen erzeugt werden")
            self.__create_combinations()
        else:
            print('NN Kombinationen müssen in Dictionary Form selbst übergeben werden')
        
    def __train(self, epoch, optimizer):
        '''
            funktion übernimmt das Training von dem in self.__model
            zwischengespeicherten NN. 
            Epoch: Jetzige Epoche in der trainiert wird (für coolen print Befehl wichtig)
            Optimizer: Optimizer mit dem Parameter des NN aus self.__model optimiert werden
        '''
        if self.cuda:
            self.__model.cuda()
            self.__model.train()
            batch_id = 0
            for key in self.train_data.keys():
                for data, target in self.train_data[key]:
                    data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0).cuda()
                    shape = target.size()[1]
                    target = target.resize(shape,1).cuda()
                    optimizer.zero_grad()
                    out = self.__model(data)
                    criterion = nn.MSELoss()
                    loss = criterion(out, target)
                    loss.backward()
                    optimizer.step()
                    #print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                    #   epoch, batch_id *len(data), len(self.train_data),
                    #00. * batch_id / len(self.train_data), loss.item()))
                    batch_id +=1
        else:
            self.__model.train()
            batch_id = 0
            for key in self.train_data.keys():
                for data, target in self.train_data[key]:
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1)
                    optimizer.zero_grad()
                    out = self.__model(data)
                    criterion = nn.MSELoss()
                    loss = criterion(out, target)
                    loss.backward()
                    optimizer.step()
                    #print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                    #    epoch, batch_id *len(data), len(self.train_data),
                    #100. * batch_id / len(self.train_data), loss.item()))
                    batch_id +=1
            
    def __test(self):
        '''
            Funktion, die das Testen des Models aus self.__model auf den übergebenen Dev-Daten 
            (self.test_data) übernimmt und den gesamt MAE für das jeweilige Modell berechnet
        '''
        total = 0
        count = 0
        result_dict = {}
        result = pd.DataFrame(columns = ['target','prediction'])
        help_dict = {}
        if self.cuda:
            self.__model.cuda()
            for key in self.test_data.keys():
                help_dict = {}
                for data, target in self.test_data[key]:
                    self.__model.eval()
                    data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1).cuda()
                    out = self.__model(data).cpu()
                    out = out.detach().numpy()
                    target = target.cpu()
                    target = target.detach().numpy()
                    total += abs(out - target[0][0])
                    help_dict[target[0][0]] = out
                    count+=1
                #Auslesen der predicteten Werte A und der zugehörigen targets y
                A = [x[0][0] for x in list((help_dict.values()))]
                y = list(help_dict.keys())
                
                #Anfügen der Werte an Result
                t = pd.DataFrame()
                t['target'] = y
                t['prediction_value'] = A
                t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
                t.reset_index(inplace = True)
                t.rename(columns = {'index':'prediction'}, inplace = True)
                t['prediction'] = t['prediction']+1
                
                
                result = result.append(t, sort = True)
                
        else:
            for raceId in self.test_data.keys():
                help_dict = {}
                for data, target in self.test_data[raceId]:
                    self.__model.eval()
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1)
                    out = self.__model(data)
                    out = out.detach().numpy()
                    target = target.detach().numpy()
                    total += abs(out - target[0][0])
                    help_dict[target[0][0]] = out
                    count+=1
                #Auslesen der predicteten Werte A und der zugehörigen targets y
                A = [x[0][0] for x in list((help_dict.values()))]
                y = list(help_dict.keys())
                
                #Anfügen der Werte an Result
                t = pd.DataFrame()
                t['target'] = y
                t['prediction_value'] = A
                t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
                t.reset_index(inplace = True)
                t.rename(columns = {'index':'prediction'}, inplace = True)
                t['prediction'] = t['prediction']+1
                
                result = result.append(t, sort = True)
        return result
    
    def get_all_information(self):
        
        print('All Model Combinations with encoding:\n', self.model_specs_combinations)
        print('Model Results:\n', self.__combination_results)
        print('Optimale Kombination:\n', self.opt_combination)
        
    def validate_combinations(self):
        
        for key, combination in self.model_specs_combinations.items():
            print("kombination, die jetzt trainiert wird", combination)
            self.__model = NetzDynamic(combination)
            optimizer = optim.Adam(self.__model.parameters(), lr = self.lr)
            #trainieren des modells
            for epoch in range(1,self.max_epochs):
                self.__train(epoch, optimizer)  
            #Aufrufen der Testfunktion
            result = self.__test()
            A = result.prediction.tolist()
            y = result.target.tolist()
            mae = MAE(A,y)
            
            
            
            self.__combination_results[key] = mae
            
        #finden der besten kombination nach minimalstem Error (MAE)
        key_min = min(self.__combination_results.keys(), key=(lambda k: self.__combination_results[k]))
        best_combination = self.model_specs_combinations[key_min]
        best_combination['mae'] = self.__combination_results[key_min]
        self.opt_combination = best_combination
        #self.__combination_overview[key] = specifics
        
        
    def __create_combinations(self):
        '''
            Funktion erzeugt Dictionarys, mit NN Modellspezifikationen, die
            später gegeneinander getestet werden sollen. Kombinationen werden
            in dem Dictionary self.model_specs_combinations unter einem 
            Schlüssel abgespeichert
        '''
        
        if self.__create_variations:
            
            if self.__pure:
                '''
                es werden mehr als ein Netz von einer bestimmten Layeranzahl erzeugt:
                wenn die Layeranzahl Range zwischen 7 und 9 liegt, self.__create_variations = True ist und
                die Variable self.__number_of_variations = 4 ist werden 4 Netze mit 7 Layern und 4 Netze
                mit 8 Layern erzeugt. Diese können dann gegeneinander getestet werden und geben eine bessere
                Übersicht über eine gute Layeranzahl. Wenn self.__pure auf True gesetzt wird, wird aus der 
                Liste mit activationfunctions [relu, sigmoid, tanh] als default 'reine' Netze erzeugt, die immmer
                nur eine der Funktionen enthält (Relu als anfang). Danach werden diese netze kopiert, nur dass die 
                Aktivierungsfunktionen überschrieben werden (ReLu wird durch sigmoid und tanh ersetzt). Zuletzt werden 
                die Funktionen wild gemischt.
                '''
                min_layer = self.__layer_range[0]
                max_layer = self.__layer_range[1]
                if min_layer == max_layer:
                    max_layer += 1
                #pure ist true, deswegen wird zu anfang eine der aktivierungsfunktionen ausgewählt, die fürs ganze netz gewählt wird
                act = random.choice(self.__activations)
                for layer in range(min_layer, max_layer): 
                    variation_counter = 0
                    while variation_counter < self.__number_of_variations:
                        variation_counter +=1 
                        dropout_counter = 0
                        act_count = 0
                        specs_dict = {}
                        middle = layer//2
                        for l in range(layer):
                            layer_specs = []
                            key = act+str(act_count)
                            act_count += 1
                            if dropout_counter == self.__dropout_number:
                                #es wurden schon ausreichend dropout layer erzeugt
                                l_ = random.choice([x for x in self.__layer_types if x not in ['dropout']])
                            else:
                                l_ = random.choice(self.__layer_types)
                                if l_ == 'dropout':
                                    dropout_counter +=1
                                    
                            if l == 0:
                                in_ = self.__input_start
                                if l_ == 'dropout':
                                    dropout_counter = dropout_counter-1
                                    l_ = 'linear'
                                range_start = self.__in_out_range[0]
                                range_end = self.__in_out_range[1]
                                out_ = random.randint(range_start, range_end)
                                layer_specs.append(l_)
                                layer_specs.append(in_)
                                layer_specs.append(out_)
                            else:
                                layer_before = specs_dict[list(specs_dict.keys())[-1]]
                                out_alt = specs_dict[list(specs_dict.keys())[-1]][2]
                                l_type = layer_before[0]
                                i_ltype = -2
                                while l_type == 'dropout':#überprüfen ob vorhergegangenes Layer ein dropout layer war
                                    #sobald das vorhergegangene nicht-dropoutlayer gefunden wurde, wird output größe übernommen
                                    layer_before = specs_dict[list(specs_dict.keys())[i_ltype]]
                                    l_type = layer_before[0]
                                    out_alt = specs_dict[list(specs_dict.keys())[i_ltype]][2]
                                    i_ltype = i_ltype -1
                                if l <= middle: #in der ertsen hälfte nimmt output zu
                                    in_ = out_alt
                                    range_start = out_alt
                                    range_end = self.__in_out_range[1]
                                    out_ = random.randint(range_start, range_end)
                                else:#in zweiter hälfte der layer nimmt output wieder ab
                                    in_ = out_alt
                                    range_start = self.__in_out_range[0]
                                    range_end = out_alt
                                    out_ = random.randint(range_start, range_end)
                                layer_specs.append(l_)
                                layer_specs.append(in_)
                                layer_specs.append(out_)
                            #if l == layer-1:
                            #    l_ = 'linear'
                            #    layer_specs = [l_,in_,self.__output_last]
                                #specs_dict['last'] = layer_specs#layer wird ohne activation gespeichert und als letztes Layer des NN gekennzeichnet
                                
                            if l == 0:
                                specs_dict['first'] = layer_specs
                            else:
                                if specs_dict[list(specs_dict.keys())[-1]][0] == 'dropout':# keine activation function bei layern direkt nach einem dropout layer
                                    key = 'no_activation'+str(act_count)
                                if l == layer -1:
                                    l_ = 'linear'
                                    layer_specs = [l_, in_, self.__output_last]
                                specs_dict[key] = layer_specs
                        key = random.randint(0,10000)
                        while key in list(self.model_specs_combinations.keys()):
                             key = random.randint(0,10000)
                        self.model_specs_combinations[key]= specs_dict   
                        print(specs_dict,'\n')
                        
                used_acts = [act]
                act_count = 0
                netze = list(self.model_specs_combinations.values())
                mixed = []
                if self.__random_activation:
                    p_ = 0
                    for netz in netze:
                        netz_neu = {}
                        for act_alt, layer_spec in netz.items():
                            if act_alt.startswith('no_activation') or act_alt.startswith('first'):
                                netz_neu[act_alt] = layer_spec
                            else:
                                act_neu = random.choice(self.__activations)
                                pp = act_neu+str(p_)
                                p_ += 1
                                netz_neu[pp]= layer_spec
                        mixed.append(netz_neu)
                for activation in self.__activations:
                    if activation in used_acts:
                        continue
                    else:
                        for netz in netze:#alle bisher erzeugten netze werden betrachtet
                            key = random.randint(0,10000)
                            while key in list(self.model_specs_combinations.keys()):
                                key = random.randint(0,10000)
                            netz_neu = {}
                            for act_alt, layer in netz.items():
                                if act_alt.startswith('no_activation') or act_alt.startswith('first'):
                                    netz_neu[act_alt] = layer
                                else:
                                    act_ = activation+str(act_count)
                                    act_count += 1
                                    netz_neu[act_] = layer
                            print(netz_neu,'\n')
                            self.model_specs_combinations[key] = netz_neu
                if len(mixed) != 0:
                    for netz in mixed:
                        print("mixed netz",netz)
                        key = random.randint(0,10000)
                        while key in list(self.model_specs_combinations.keys()):
                            key = random.randint(0,10000)
                        self.model_specs_combinations[key] = netz
                print("alle kombinationen nach create combination:", self.model_specs_combinations)
            else:
                raise Exception('please set pure_activations to True, False not implemented')
                    
        else:
            min_layer = self.__layer_range[0]
            max_layer = self.__layer_range[1]
            if min_layer == max_layer:
                max_layer += 1
            for layer in range(min_layer, max_layer): 
                
                dropout_counter = 0
                act_count = 0
                specs_dict = {}
                middle = layer//2
                for l in range(layer):
                    layer_specs = []
                    if self.__random_activation:#random activation pick ist aktiviert
                        act = random.choice(self.__activations)
                        key = act+str(act_count)
                        act_count += 1
                        if dropout_counter == self.__dropout_number:
                            #es wurden schon ausreichend dropout layer erzeugt
                            l_ = random.choice([x for x in self.__layer_types if x not in ['dropout']])
                        else:
                            l_ = random.choice(self.__layer_types)
                            if l_ == 'dropout':
                                dropout_counter +=1
                                
                        if l == 0:
                            in_ = self.__input_start
                            if l_ == 'dropout':
                                dropout_counter = dropout_counter-1
                                l_ = 'linear'
                            range_start = self.__in_out_range[0]
                            range_end = self.__in_out_range[1]
                            out_ = random.randint(range_start, range_end)
                            layer_specs.append(l_)
                            layer_specs.append(in_)
                            layer_specs.append(out_)
                        else:
                            layer_before = specs_dict[list(specs_dict.keys())[-1]]
                            out_alt = specs_dict[list(specs_dict.keys())[-1]][2]
                            l_type = layer_before[0]
                            i_ltype = -2
                            while l_type == 'dropout':#überprüfen ob vorhergegangenes Layer ein dropout layer war
                                #sobald das vorhergegangene nicht-dropoutlayer gefunden wurde, wird output größe übernommen
                                layer_before = specs_dict[list(specs_dict.keys())[i_ltype]]
                                l_type = layer_before[0]
                                out_alt = specs_dict[list(specs_dict.keys())[i_ltype]][2]
                                i_ltype = i_ltype -1
                            if l <= middle: #in der ertsen hälfte nimmt output zu
                                in_ = out_alt
                                range_start = out_alt
                                range_end = self.__in_out_range[1]
                                out_ = random.randint(range_start, range_end)
                            else:#in zweiter hälfte der layer nimmt output wieder ab
                                in_ = out_alt
                                range_start = self.__in_out_range[0]
                                range_end = out_alt
                                out_ = random.randint(range_start, range_end)
                            layer_specs.append(l_)
                            layer_specs.append(in_)
                            layer_specs.append(out_)
                        #if l == layer-1:
                        #    l_ = 'linear'
                        #    layer_specs = [l_,in_,self.__output_last]
                        #    specs_dict['last'] = layer_specs#layer wird ohne activation gespeichert und als letztes Layer des NN gekennzeichnet
                            
                        #elif l == 0:
                        if l == 0:
                            specs_dict['first'] = layer_specs
                        else:
                            #if l_ == 'dropout':#keine activation function bei dropout layern
                            #    key = 'no_activation'+str(act_count)
                            if specs_dict[list(specs_dict.keys())[-1]][0] == 'dropout':# keine activation function bei layern direkt nach einem dropout layer
                                key = 'no_activation'+str(act_count)
                            if l == layer -1:
                                l_ = 'linear'
                                layer_specs = [l_, in_, self.__output_last]
                            specs_dict[key] = layer_specs
                key = random.randint(0,10000)
                while key in list(self.model_specs_combinations.keys()):
                     key = random.randint(0,10000)
                self.model_specs_combinations[key]= specs_dict   
                print(specs_dict)

                
class HP_Optimizer(object):
    
    def __init__(self, lr_range = (0.0001,0.0001), step_size = 0.0001, max_epochs = (2,2), opt = 'Adam', cuda = True, dynamic = False, dyn_combination = {}):
        
        self.__model = Netz()#Modellklasse, die verwendet wird
        self.__lr = lr_range
        self.__epochs = max_epochs
        self.__optimizer = opt
        self.__steps = step_size
        self.__combination_results = {}
        self.__combination_overview = {}
        self.train_data = None
        self.test_data = None
        self.cuda = cuda
        self.opt_combination = {}
        self.__dynamic = dynamic
        self.__dyn_combination = dyn_combination
        
        
    def validate_combinations(self):
        
        specifics = {}
        if self.__optimizer == 'Adam':
            
            #definieren der range für die lernratenoptimierung
            if isinstance(self.__lr, tuple):
                lr_s = self.__lr[0]
                lr_e = self.__lr[1]
                #wurde eine range für die anzahl der epochen übergeben?
                if self.__epochs[0] == self.__epochs[1]:
                    #hyperparamter epochenanzahl wird nicht optimiert
                    max_epoch = self.__epochs[0]
                    if lr_s == lr_e:
                        #es ist keine range für die lernrate gegeben, in der diese optimiert werden soll
                        print('Parameter Epochen und Lernrate können nicht optimiert werden, da kein Intervall übergeben wurde')
                        #setzen des optimizers als Adam und erzeugen des Modells
                        if self.__dynamic:
                            self.__model = NetzDynamic(self.__dyn_combination)
                        else:
                            self.__model = Netz()
                        optimizer = optim.Adam(self.__model.parameters(), lr = lr_s)
                        for epoch in range(1,max_epoch):
                            self.__train(epoch, optimizer)     
                        result = self.__test()
                        A = result.prediction.tolist()
                        y = result.target.tolist()
                        mae = MAE(A,y)
                        specifics = {}
                        specifics['lr'] = lr_s
                        specifics['epochen'] = max_epoch
                        key = random.randint(0,10000)
                        while key in list(self.__combination_results.keys()):
                             key = random.randint(0,10000)
                        self.__combination_results[key] = mae
                        self.__combination_overview[key] = specifics 
                    else:
                        for l in np.arange(lr_s,lr_e, self.__steps):
                            #setzen des optimizers als Adam und erzeugen des Modells
                            if self.__dynamic:
                                self.__model = NetzDynamic(self.__dyn_combination)
                            else:
                                self.__model = Netz()
                            optimizer = optim.Adam(self.__model.parameters(), lr = l)
                            #trainieren des modells
                            for epoch in range(1,max_epoch):
                                self.__train(epoch, optimizer)  
                            result = self.__test()
                            A = result.prediction.tolist()
                            y = result.target.tolist()
                            mae = MAE(A,y)
                            specifics = {}
                            specifics['lr'] = l
                            specifics['epochen'] = max_epoch
                            #abspeichern der gewonnenen informationen (MAE nach lr und anzahl durchgeführter epochen)
                            key = random.randint(0,10000)
                            while key in list(self.__combination_results.keys()):
                                 key = random.randint(0,10000)
                            self.__combination_results[key] = mae
                            self.__combination_overview[key] = specifics
                else:
                    for max_epoch in range(self.__epochs[0], self.__epochs[1]):
                        #definieren der range für die lernratenoptimierung
                        lr_s = self.__lr[0]
                        lr_e = self.__lr[1]
                        #hyperparamter epochenanzahl wird nicht optimiert
                        if lr_s == lr_e:
                            #es ist keine range für die lernrate gegeben, in der diese optimiert werden soll
                            #print('Parameter Epochen und Lernrate können nicht optimiert werden, da kein Intervall übergeben wurde')
                            if self.__dynamic:
                                self.__model = NetzDynamic(self.__dyn_combination)
                            else:
                                self.__model = Netz()
                            optimizer = optim.Adam(self.__model.parameters(), lr = lr_s)
                            for epoch in range(1,max_epoch):
                                self.__train(epoch, optimizer)       
                            result = self.__test()
                            A = result.prediction.tolist()
                            y = result.target.tolist()
                            mae = MAE(A,y)
                            specifics = {}
                            specifics['lr'] = lr_s
                            specifics['epochen'] = max_epoch
                            key = random.randint(0,10000)
                            while key in list(self.__combination_results.keys()):
                                 key = random.randint(0,10000)  
                            self.__combination_results[key] = mae
                            self.__combination_overview[key] = specifics          
                        else:
                            for l in np.arange(lr_s,lr_e, self.__steps):
                                if self.__dynamic:
                                    self.__model = NetzDynamic(self.__dyn_combination)
                                else:
                                    self.__model = Netz()
                                optimizer = optim.Adam(self.__model.parameters(), lr = l)
                                #trainieren des modells
                                for epoch in range(1,max_epoch):
                                    self.__train(epoch, optimizer)  
                                result = self.__test()
                                A = result.prediction.tolist()
                                y = result.target.tolist()
                                mae = MAE(A,y)
                                specifics = {}
                                specifics['lr'] = l
                                specifics['epochen'] = max_epoch
                                #abspeichern der gewonnenen informationen (MAE nach lr und anzahl durchgeführter epochen)
                                key = random.randint(0,10000)
                                while key in list(self.__combination_results.keys()):
                                     key = random.randint(0,10000)
                                self.__combination_results[key] = mae
                                self.__combination_overview[key] = specifics
                #finden der besten kombination nach minimalstem Error (MAE)
                key_min = min(self.__combination_results.keys(), key=(lambda k: self.__combination_results[k]))
                best_combination = self.__combination_overview[key_min]
                best_combination['mae'] = self.__combination_results[key_min]
                self.opt_combination = best_combination
            elif isinstance(self.__lr, list):
                #wurde eine range für die anzahl der epochen übergeben?
                if self.__epochs[0] == self.__epochs[1]:
                    #hyperparamter epochenanzahl wird nicht optimiert
                    max_epoch = self.__epochs[0]
                    if len(self.__lr) ==1:
                        #es ist keine range für die lernrate gegeben, in der diese optimiert werden soll
                        print('Parameter Epochen und Lernrate können nicht optimiert werden, da kein Intervall übergeben wurde')
                        #setzen des optimizers als Adam und erzeugen des Modells
                        if self.__dynamic:
                            self.__model = NetzDynamic(self.__dyn_combination)
                        else:
                            self.__model = Netz()
                        optimizer = optim.Adam(self.__model.parameters(), lr = self.__lr[0])
                        for epoch in range(1,max_epoch):
                            self.__train(epoch, optimizer)     
                        result = self.__test()
                        A = result.prediction.tolist()
                        y = result.target.tolist()
                        mae = MAE(A,y)
                        specifics = {}
                        specifics['lr'] = self.__lr[0]
                        specifics['epochen'] = max_epoch
                        key = random.randint(0,10000)
                        while key in list(self.__combination_results.keys()):
                             key = random.randint(0,10000)
                        self.__combination_results[key] = mae
                        self.__combination_overview[key] = specifics 
                    else:
                        for l in self.__lr:
                            #setzen des optimizers als Adam und erzeugen des Modells
                            if self.__dynamic:
                                self.__model = NetzDynamic(self.__dyn_combination)
                            else:
                                self.__model = Netz()
                            optimizer = optim.Adam(self.__model.parameters(), lr = l)
                            #trainieren des modells
                            for epoch in range(1,max_epoch):
                                self.__train(epoch, optimizer)  
                            result = self.__test()
                            A = result.prediction.tolist()
                            y = result.target.tolist()
                            mae = MAE(A,y)
                            specifics = {}
                            specifics['lr'] = l
                            specifics['epochen'] = max_epoch
                            #abspeichern der gewonnenen informationen (MAE nach lr und anzahl durchgeführter epochen)
                            key = random.randint(0,10000)
                            while key in list(self.__combination_results.keys()):
                                 key = random.randint(0,10000)
                            self.__combination_results[key] = mae
                            self.__combination_overview[key] = specifics
                else:
                    for max_epoch in range(self.__epochs[0], self.__epochs[1]):
                        #definieren der range für die lernratenoptimierung
                        lr_s = self.__lr[0]
                        lr_e = self.__lr[1]
                        #hyperparamter epochenanzahl wird nicht optimiert
                        if len(self.__lr) == 1:
                            #es ist keine range für die lernrate gegeben, in der diese optimiert werden soll
                            #print('Parameter Epochen und Lernrate können nicht optimiert werden, da kein Intervall übergeben wurde')
                            if self.__dynamic:
                                self.__model = NetzDynamic(self.__dyn_combination)
                            else:
                                self.__model = Netz()
                            optimizer = optim.Adam(self.__model.parameters(), lr = self.__lr[0])
                            for epoch in range(1,max_epoch):
                                self.__train(epoch, optimizer)       
                            result = self.__test()
                            A = result.prediction.tolist()
                            y = result.target.tolist()
                            mae = MAE(A,y)
                            specifics = {}
                            specifics['lr'] = self.__lr[0]
                            specifics['epochen'] = max_epoch
                            key = random.randint(0,10000)
                            while key in list(self.__combination_results.keys()):
                                 key = random.randint(0,10000)  
                            self.__combination_results[key] = mae
                            self.__combination_overview[key] = specifics          
                        else:
                            for l in self.__lr:
                                if self.__dynamic:
                                    self.__model = NetzDynamic(self.__dyn_combination)
                                else:
                                    self.__model = Netz()
                                optimizer = optim.Adam(self.__model.parameters(), lr = l)
                                #trainieren des modells
                                for epoch in range(1,max_epoch):
                                    self.__train(epoch, optimizer)  
                                result = self.__test()
                                A = result.prediction.tolist()
                                y = result.target.tolist()
                                mae = MAE(A,y)
                                specifics = {}
                                specifics['lr'] = l
                                specifics['epochen'] = max_epoch
                                #abspeichern der gewonnenen informationen (MAE nach lr und anzahl durchgeführter epochen)
                                key = random.randint(0,10000)
                                while key in list(self.__combination_results.keys()):
                                     key = random.randint(0,10000)
                                self.__combination_results[key] = mae
                                self.__combination_overview[key] = specifics
                #finden der besten kombination nach minimalstem Error (MAE)
                key_min = min(self.__combination_results.keys(), key=(lambda k: self.__combination_results[k]))
                best_combination = self.__combination_overview[key_min]
                best_combination['mae'] = self.__combination_results[key_min]
                self.opt_combination = best_combination
                
        else:
            raise ('No valid optimizer given! Try Adam for example!')
            
    def __train(self, epoch, optimizer):
        if self.cuda:
            self.__model.cuda()
            self.__model.train()
            batch_id = 0
            for key in self.train_data.keys():
                for data, target in self.train_data[key]:
                    data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0).cuda()
                    shape = target.size()[1]
                    target = target.resize(shape,1).cuda()
                    optimizer.zero_grad()
                    out = self.__model(data)
                    #print("Out: ", out, out.size())
                    #print("Target: ", target, target.size())
                    criterion = nn.MSELoss()
                    loss = criterion(out, target)
                    loss.backward()
                    optimizer.step()
                    #rint("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                    #   epoch, batch_id *len(data), len(self.train_data),
                    #00. * batch_id / len(self.train_data), loss.item()))
                    batch_id +=1
        else:
            self.__model.train()
            batch_id = 0
            for key in self.train_data.keys():
                for data, target in self.train_data[key]:
                    #data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)#.cuda()
                    shape = target.size()[1]
                    target = target.resize(shape,1)#.cuda()
                    optimizer.zero_grad()
                    out = self.__model(data)
                    #print("Out: ", out, out.size())
                    #print("Target: ", target, target.size())
                    criterion = nn.MSELoss()
                    loss = criterion(out, target)
                    loss.backward()
                    optimizer.step()
                    #print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                    #    epoch, batch_id *len(data), len(train_data),
                    #100. * batch_id / len(train_data), loss.item()))
                    batch_id +=1
                    
            
    def __test(self):
        total = 0
        count = 0
        result_dict = {}
        result = pd.DataFrame(columns = ['target','prediction'])
        help_dict = {}
        if self.cuda:
            self.__model.cuda()
            for key in self.test_data.keys():
                #print(key)
                help_dict = {}
                for data, target in self.test_data[key]:
                    self.__model.eval()
                    #files.listdir(path)
                    data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1).cuda()
                    out = self.__model(data).cpu()
                    #print(out)
                    out = out.detach().numpy()
                    #out = np.round(out)
                    target = target.cpu()
                    target = target.detach().numpy()
                    #print(data)
                    #print(data["driverId"])
                    total += abs(out - target[0][0])
                    #print("current_position: ", data[0][0].item())
                    #print("Output: ", out)
                    #print("Target: ", target)
                    help_dict[target[0][0]] = out
                    #print("Difference: ", out - target)
                    count+=1
                #Auslesen der predicteten Werte A und der zugehörigen targets y
                A = [x[0][0] for x in list((help_dict.values()))]
                y = list(help_dict.keys())
                
                #Anfügen der Werte an Result
                t = pd.DataFrame()
                t['target'] = y
                t['prediction_value'] = A
                t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
                t.reset_index(inplace = True)
                t.rename(columns = {'index':'prediction'}, inplace = True)
                t['prediction'] = t['prediction']+1
                
                
                result = result.append(t, sort = True)
                
        else:
            for raceId in self.test_data.keys():
                #print(key)
                help_dict = {}
                for data, target in self.test_data[raceId]:
                    self.__model.eval()
                    #files.listdir(path)
                    #data = data.cuda()
                    target = torch.Tensor(target).unsqueeze(0)
                    shape = target.size()[1]
                    target = target.resize(shape,1)#.cuda()
                    out = self.__model(data)#.cpu()
                    #print(out)
                    out = out.detach().numpy()
                    #out = np.round(out)
                    #target = target.cpu()
                    target = target.detach().numpy()
                    #print(data)
                    #print(data["driverId"])
                    total += abs(out - target[0][0])
                    #print("current_position: ", data[0][0].item())
                    #print("Output: ", out)
                    #print("Target: ", target)
                    help_dict[target[0][0]] = out
                    #print("Difference: ", out - target)
                    count+=1
                #Auslesen der predicteten Werte A und der zugehörigen targets y
                A = [x[0][0] for x in list((help_dict.values()))]
                y = list(help_dict.keys())
                
                #Anfügen der Werte an Result
                t = pd.DataFrame()
                t['target'] = y
                t['prediction_value'] = A
                t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
                t.reset_index(inplace = True)
                t.rename(columns = {'index':'prediction'}, inplace = True)
                t['prediction'] = t['prediction']+1
                
                result = result.append(t, sort = True)
        return result
         
            
    def get_all_information(self):
        
        print('Chosen Model:',self.__model)
        print('Learningrate Range:',self.__lr)
        print('Maximum Epochs:', self.__epochs)
        print('Chosen Optimizer:', self.__optimizer)
        print('Result Encoding:', self.__combination_overview)
        print('Results:', self.__combination_results)
        print('Optimale Kombination:', self.opt_combination)
        
    def help(self):
        print('Parameters with defaults:\nlr_range --> (0.0001,0.0001),\nstep_size--> 0.0001,\nmax_epochs-->(2,2),\nopt-->"Adam",\ncuda=True')
        print('lr_range: Tupel with learnrate range')
        print('step_size: float/int for step_size of learnrate')
        print('max_epochs: Tupel with number of epochs range')
        print('opt: Optimizer (by default Adam)')
        print('cuda: True/False if cuda should be used, default = True\n')
        print('Attributes:')
        print('set self.train_data as dictionary with races (form: {raceId: race(dataframe)})')
        print('set self.test_data as dictionary with races (form: {raceId: race(dataframe)})')
        print('self.opt_combination: Dictionary which contains the best combination of the given parameters\n')
        print('Methods:')
        print('call self.validate_combination() to compare all combinations')
        print('get all information/results with self.get_all_information()')

#### Finden des "optimalsten" Netzes  
**Ausführungsdauer: ~ 9 Stunden**<br>
Aufrufen des Layeroptimizers, um verschiedene Neuronale Netze gegeneinander zu testen, mit verschiedenen Layeranzahlen, und Input und Output Neuronen. Gemeinsam haben die Netze, dass bis zur Mitte die Anzahl Neuronen zunimmt, und dann zum letzten Layer hin wieder abnimmt.
<br>Es wird das Netz ausgewählt, welches den niedrigsten MAE auf dem Dev Datensatz hat. Ziel ist es durch Aufrufen dieser Klasse die beste Layeranzahl-Aktivierungsfunktionen-Kombination für den Use Case zu finden (anhand vorgegebener einschränkender Paramter). Da die Anzahl der Neuronen jedes Mal zufällig implementiert wird, und dieser Faktor nur wenig eingeschränkt ist, kann hier mit jedem neuen Aufruf der Klasse ein anderes Netz als optimal ausgewählt werden. Das optimalste Netz richtet sich auch stark nach dem train-dev-test splitting des Datensatzes.

In [ ]:
import time
opt_combination = []
for k in range(30): 
    start_time = time.time()
    if cuda.lower() == 'y':
        l = HP_Layer_Optimizer(layer_range=(7,12),
                           max_epochs = 4,
                           input_start = 52,
                           random_activation=True,
                           create_combinations=True, 
                           create_variations = True, 
                           num_variations = 1,#5
                           pure_activations = True,
                           cuda = True)
    else:
        l = HP_Layer_Optimizer(layer_range=(7,12),
                           max_epochs = 4,
                           input_start = 52, 
                           random_activation=True,
                           create_combinations=True, 
                           create_variations = True, 
                           num_variations = 1,
                           pure_activations = True,
                           cuda = False)
    l.train_data = train_T
    l.test_data = dev_T
    l.validate_combinations()
    l.get_all_information()
    opt_combination.append(l.opt_combination)
    print('execution time in s:', time.time() -start_time)

0 tes netz
in constructor bevor die kombinationen erzeugt werden
{'first': ['linear', 52, 199], 'sigmoid1': ['dropout', 199, 200], 'no_activation3': ['linear', 199, 199], 'sigmoid3': ['linear', 199, 200], 'sigmoid4': ['linear', 200, 198], 'sigmoid5': ['linear', 198, 58], 'sigmoid6': ['linear', 58, 1]} 

{'first': ['linear', 52, 154], 'sigmoid1': ['dropout', 154, 194], 'no_activation3': ['linear', 154, 187], 'sigmoid3': ['linear', 187, 198], 'sigmoid4': ['linear', 198, 200], 'sigmoid5': ['linear', 200, 170], 'sigmoid6': ['linear', 170, 163], 'sigmoid7': ['linear', 163, 1]} 

{'first': ['linear', 52, 74], 'sigmoid1': ['dropout', 74, 157], 'no_activation3': ['linear', 74, 169], 'sigmoid3': ['linear', 169, 178], 'sigmoid4': ['linear', 178, 193], 'sigmoid5': ['linear', 193, 102], 'sigmoid6': ['linear', 102, 46], 'sigmoid7': ['linear', 46, 43], 'sigmoid8': ['linear', 43, 1]} 

{'first': ['linear', 52, 33], 'sigmoid1': ['dropout', 33, 33], 'no_activation3': ['linear', 33, 82], 'sigmoid3': ['l

/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.

kombination, die jetzt trainiert wird {'first': ['linear', 52, 154], 'sigmoid1': ['dropout', 154, 194], 'no_activation3': ['linear', 154, 187], 'sigmoid3': ['linear', 187, 198], 'sigmoid4': ['linear', 198, 200], 'sigmoid5': ['linear', 200, 170], 'sigmoid6': ['linear', 170, 163], 'sigmoid7': ['linear', 163, 1]}


/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.

kombination, die jetzt trainiert wird {'first': ['linear', 52, 74], 'sigmoid1': ['dropout', 74, 157], 'no_activation3': ['linear', 74, 169], 'sigmoid3': ['linear', 169, 178], 'sigmoid4': ['linear', 178, 193], 'sigmoid5': ['linear', 193, 102], 'sigmoid6': ['linear', 102, 46], 'sigmoid7': ['linear', 46, 43], 'sigmoid8': ['linear', 43, 1]}


...

/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.

kombination, die jetzt trainiert wird {'first': ['linear', 52, 85], 'sigmoid26': ['linear', 85, 113], 'sigmoid27': ['dropout', 113, 148], 'no_activation4': ['linear', 113, 135], 'sigmoid28': ['linear', 135, 152], 'sigmoid29': ['linear', 152, 159], 'tanh30': ['linear', 159, 54], 'tanh31': ['linear', 54, 39], 'tanh32': ['linear', 39, 36], 'relu33': ['linear', 36, 33], 'sigmoid34': ['linear', 33, 1]}


/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.

All Model Combinations with encoding:
 {10000: {'first': ['linear', 52, 107], 'relu1': ['dropout', 107, 180], 'no_activation3': ['linear', 107, 148], 'relu3': ['linear', 148, 165], 'relu4': ['linear', 165, 65], 'relu5': ['linear', 65, 51], 'relu6': ['linear', 51, 1]}, 7475: {'first': ['linear', 52, 142], 'relu1': ['dropout', 142, 157], 'no_activation3': ['linear', 142, 167], 'relu3': ['linear', 167, 171], 'relu4': ['linear', 171, 176], 'relu5': ['linear', 176, 104], 'relu6': ['linear', 104, 91], 'relu7': ['linear', 91, 1]}, 9584: {'first': ['linear', 52, 44], 'relu1': ['dropout', 44, 84], 'no_activation3': ['linear', 44, 135], 'relu3': ['linear', 135, 137], 'relu4': ['linear', 137, 180], 'relu5': ['linear', 180, 55], 'relu6': ['linear', 55, 31], 'relu7': ['linear', 31, 30], 'relu8': ['linear', 30, 1]}, 4218: {'first': ['linear', 52, 126], 'relu1': ['linear', 126, 138], 'relu2': ['dropout', 138, 156], 'no_activation4': ['linear', 138, 138], 'relu4': ['linear', 138, 197], 'relu5': ['line

/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")


30 als gut eingestufte Netze sind nun in der Liste opt_combination abgespeichert. Diese können im nächsten Schritt verwendet werden, um die Lernrate und Epochenanzahl jedes dieser Netze zu optimieren.<br>
Zunächst wird jedoch eine kurze Übersicht gegeben, wie viele Layer jedes der Netze hat, welche Aktivierungsfunktionen und an welcher Stelle sich das Dropout-Layer befindet.

In [ ]:
print(opt_combination)

[{'first': ['linear', 52, 154], 'relu5': ['dropout', 154, 194], 'no_activation3': ['linear', 154, 187], 'relu6': ['linear', 187, 198], 'relu7': ['linear', 198, 200], 'relu8': ['linear', 200, 170], 'relu9': ['linear', 170, 163], 'relu10': ['linear', 163, 1], 'mae': 1.6627906976744187}, {'first': ['linear', 52, 162], 'relu1': ['linear', 162, 185], 'relu2': ['linear', 185, 191], 'relu3': ['linear', 191, 194], 'relu4': ['dropout', 194, 200], 'no_activation6': ['linear', 194, 197], 'relu6': ['linear', 197, 171], 'relu7': ['linear', 171, 108], 'relu8': ['linear', 108, 40], 'relu9': ['linear', 40, 1], 'mae': 1.6666666666666667}, {'first': ['linear', 52, 183], 'relu0': ['linear', 183, 200], 'sigmoid1': ['linear', 200, 200], 'relu2': ['dropout', 200, 200], 'no_activation5': ['linear', 200, 42], 'sigmoid3': ['linear', 42, 30], 'relu4': ['linear', 30, 1], 'mae': 1.6356589147286822}, {'first': ['linear', 52, 148], 'sigmoid5': ['linear', 148, 194], 'tanh6': ['linear', 194, 200], 'tanh7': ['dropout'

In [2]:
opt_combination

[{'first': ['linear', 52, 154],
  'relu5': ['dropout', 154, 194],
  'no_activation3': ['linear', 154, 187],
  'relu6': ['linear', 187, 198],
  'relu7': ['linear', 198, 200],
  'relu8': ['linear', 200, 170],
  'relu9': ['linear', 170, 163],
  'relu10': ['linear', 163, 1],
  'mae': 1.6627906976744187},
 {'first': ['linear', 52, 162],
  'relu1': ['linear', 162, 185],
  'relu2': ['linear', 185, 191],
  'relu3': ['linear', 191, 194],
  'relu4': ['dropout', 194, 200],
  'no_activation6': ['linear', 194, 197],
  'relu6': ['linear', 197, 171],
  'relu7': ['linear', 171, 108],
  'relu8': ['linear', 108, 40],
  'relu9': ['linear', 40, 1],
  'mae': 1.6666666666666667},
 {'first': ['linear', 52, 183],
  'relu0': ['linear', 183, 200],
  'sigmoid1': ['linear', 200, 200],
  'relu2': ['dropout', 200, 200],
  'no_activation5': ['linear', 200, 42],
  'sigmoid3': ['linear', 42, 30],
  'relu4': ['linear', 30, 1],
  'mae': 1.6356589147286822},
 {'first': ['linear', 52, 148],
  'sigmoid5': ['linear', 148, 1

In [ ]:
#generelle Informationen über die zuvor erzeugten Netze werden in auswertung zusammengetragen und abgespeichert
auswertung = pd.DataFrame(columns = ['relu', 'sigmoid', 'tanh', 'layer_sum', 'dropout_loc','mae'])
idx = 0
for combination in opt_combination:
    relu = 0
    sigmoid = 0
    tanh = 0
    layer_sum = 0
    dropout_loc = 0
    mae = 0
    layer_count = 1
    for act, layer in combination.items():
        if act == "mae":
            mae = layer
        else:
            if act.startswith('relu'):
                relu += 1
            elif act.startswith('sigmoid'):
                sigmoid += 1
            elif act.startswith('tanh'):
                tanh += 1
            else:
                pass
            if layer[0] == "dropout":
                dropout_loc = layer_count
        layer_count += 1
    layer_sum = len(list(combination.keys()))-1
    row = [relu, sigmoid, tanh, layer_sum, dropout_loc, mae]
    auswertung.loc[idx, :] = row
    idx += 1
auswertung

relu sigmoid tanh layer_sum dropout_loc      mae
0     6       0    0         8           2  1.66279
1     8       0    0        10           5  1.66667
2     3       2    0         7           4  1.63566
3     2       2    2         8           4  1.54651
4     3       4    2        11           2  1.65504
5     0       0    6         8           3  1.65116
6     4       2    2        10           5  1.52326
7     0       0    5         7           3  1.64729
8     6       2    0        10           3  1.61628
9     4       1    0         7           2  1.64729
10    2       1    3         8           7  1.59302
11    8       0    0        10           7  1.63953
12    6       0    1         9           2  1.60078
13    6       0    0         8           4  1.64729
14    6       0    0         8           3  1.66279
15    2       0    3         7           3  1.57364
16    1       2    2         7           2  1.64341
17    4       3    1        10           3  1.61628
18    4       1    2         9           2  1.65116
19    0       0    5         7           5  1.55039
20    2       1    2         7           3  1.57364
21    5       2    1        10           2  1.63566
22    7       0    0         9           4  1.63953
23    0       0    6         8           3  1.64341
24    3       1    1         7           3  1.60078
25    4       0    4        10           2  1.66667
26    5       0    0         7           3  1.65891
27    2       1    2         7           5   1.5814
28    7       0    0         9           4  1.63566
29    9       0    0        11           3  1.66279

In [ ]:
auswertung.to_csv("auswertung_netze.csv",sep = ";")

#### Optimieren der Lernrate und Trainingsepochenanzahl
**Ausführungsdauer: ~ 8h**<br>
Paralleles Aufrufen des Optimierers, übergeben der zuvor erzeugten Dev- und Trainingsdatensätze, angeben der Intervalle für die die Hyperparameter getestet werden sollen (Lernrate und Epochenanzahl). Für die 30 dynamischen Modelle wird jeweils das Dictionary übergeben, welches von dem vorhergegangenen Layer Optimizer am besten bewertet wurde und die Variable dynamic auf True gesetzt (default False). Der "normale" HP_Optimizer basiert auf der Klasse Netz().

In [ ]:
import time
dynamische_netze = []
#"korrigieren" der netz dictionarys --> mae aus den keys entfernen 
for netz in opt_combination:
    opt_={}
    for key in netz.keys():
        if key != 'mae':#mae wird noch in dictionary von HP_Optimizer hinzugefügt und muss entfernt werden
            opt_[key] = netz[key]
    dynamische_netze.append(opt_)
    
#alle dynamisch erzeugten netze werden auf lernrate und trainingsepocen optimiert
idx = 0
auswertung['mae_l'] = 0
auswertung['lr'] = 0
auswertung['epochs'] = 0
for netz in dynamische_netze:
    print(idx, 'netz wird optimiert')
    start_time = time.time()
    #überprüfen ob cuda verwendet werden soll, dann Aufruf des Optimizers für beide Netze
    if cuda.lower() == 'y':
        h_dynamic = HP_Optimizer(lr_range = [0.0001,0.0016],step_size = 0.0005, max_epochs=(7,12),cuda = True, dynamic = True, dyn_combination = netz)
    else:
        h_dynamic = HP_Optimizer(lr_range = [0.0001,0.001],step_size = 0.0005, max_epochs=(7,12),cuda = False, dynamic = True, dyn_combination = netz)
    h_dynamic.train_data = train_T
    h_dynamic.test_data = dev_T
    h_dynamic.validate_combinations()
    print('\n',25*'=','\n')
    print('Dynamisches Netz:\n')
    h_dynamic.get_all_information()
    
    #hinzufüge von hier ermittelten Informationen (lr, neuer mae) zu auswertung
    max_epochs_dyn = h_dynamic.opt_combination['epochen']
    lr_dynamic = h_dynamic.opt_combination['lr']
    mae_dynamic = h_dynamic.opt_combination["mae"]
    auswertung.loc[idx, 'mae_l'] = mae_dynamic
    auswertung.loc[idx, 'lr'] = lr_dynamic
    auswertung.loc[idx, 'epochs'] = max_epochs_dyn
    netz["epochen"] = max_epochs_dyn
    netz["lr"] = lr_dynamic
    netz["mae"] = mae_dynamic
    dynamische_netze[idx] = netz
    idx += 1
    time_dif = time.time()-start_time
    print('execution time layer optimizer in s:', time_dif)
auswertung

0 netz wird optimiert


/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.



Dynamisches Netz:

Chosen Model: NetzDynamic(
  (layers): ModuleList(
    (0): Linear(in_features=52, out_features=154, bias=True)
    (1): Dropout(p=0.5, inplace=False)
    (2): Linear(in_features=154, out_features=187, bias=True)
    (3): Linear(in_features=187, out_features=198, bias=True)
    (4): Linear(in_features=198, out_features=200, bias=True)
    (5): Linear(in_features=200, out_features=170, bias=True)
    (6): Linear(in_features=170, out_features=163, bias=True)
    (7): Linear(in_features=163, out_features=1, bias=True)
  )
)
Learningrate Range: [0.0001, 0.0016]
Maximum Epochs: (7, 12)
Chosen Optimizer: Adam
Result Encoding: {6921: {'lr': 0.0001, 'epochen': 7}, 1899: {'lr': 0.0016, 'epochen': 7}, 9279: {'lr': 0.0001, 'epochen': 8}, 6000: {'lr': 0.0016, 'epochen': 8}, 2707: {'lr': 0.0001, 'epochen': 9}, 7935: {'lr': 0.0016, 'epochen': 9}, 2535: {'lr': 0.0001, 'epochen': 10}, 9609: {'lr': 0.0016, 'epochen': 10, 'mae': 1.2286821705426356}, 7584: {'lr': 0.0001, 'epochen': 1

/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.



Dynamisches Netz:

Chosen Model: NetzDynamic(
  (layers): ModuleList(
    (0): Linear(in_features=52, out_features=162, bias=True)
    (1): Linear(in_features=162, out_features=185, bias=True)
    (2): Linear(in_features=185, out_features=191, bias=True)
    (3): Linear(in_features=191, out_features=194, bias=True)
    (4): Dropout(p=0.5, inplace=False)
    (5): Linear(in_features=194, out_features=197, bias=True)
    (6): Linear(in_features=197, out_features=171, bias=True)
    (7): Linear(in_features=171, out_features=108, bias=True)
    (8): Linear(in_features=108, out_features=40, bias=True)
    (9): Linear(in_features=40, out_features=1, bias=True)
  )
)
Learningrate Range: [0.0001, 0.0016]
Maximum Epochs: (7, 12)
Chosen Optimizer: Adam
Result Encoding: {7807: {'lr': 0.0001, 'epochen': 7}, 1364: {'lr': 0.0016, 'epochen': 7}, 9006: {'lr': 0.0001, 'epochen': 8}, 3630: {'lr': 0.0016, 'epochen': 8, 'mae': 1.2286821705426356}, 6968: {'lr': 0.0001, 'epochen': 9}, 3410: {'lr': 0.0016, 

...



Dynamisches Netz:

Chosen Model: NetzDynamic(
  (layers): ModuleList(
    (0): Linear(in_features=52, out_features=35, bias=True)
    (1): Linear(in_features=35, out_features=198, bias=True)
    (2): Linear(in_features=198, out_features=198, bias=True)
    (3): Dropout(p=0.5, inplace=False)
    (4): Linear(in_features=198, out_features=199, bias=True)
    (5): Linear(in_features=199, out_features=93, bias=True)
    (6): Linear(in_features=93, out_features=82, bias=True)
    (7): Linear(in_features=82, out_features=78, bias=True)
    (8): Linear(in_features=78, out_features=1, bias=True)
  )
)
Learningrate Range: [0.0001, 0.0016]
Maximum Epochs: (7, 12)
Chosen Optimizer: Adam
Result Encoding: {4877: {'lr': 0.0001, 'epochen': 7}, 6509: {'lr': 0.0016, 'epochen': 7}, 3041: {'lr': 0.0001, 'epochen': 8}, 333: {'lr': 0.0016, 'epochen': 8}, 7306: {'lr': 0.0001, 'epochen': 9}, 7501: {'lr': 0.0016, 'epochen': 9}, 7998: {'lr': 0.0001, 'epochen': 10}, 9573: {'lr': 0.0016, 'epochen': 10}, 9553: {

/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.



Dynamisches Netz:

Chosen Model: NetzDynamic(
  (layers): ModuleList(
    (0): Linear(in_features=52, out_features=85, bias=True)
    (1): Linear(in_features=85, out_features=113, bias=True)
    (2): Dropout(p=0.5, inplace=False)
    (3): Linear(in_features=113, out_features=135, bias=True)
    (4): Linear(in_features=135, out_features=152, bias=True)
    (5): Linear(in_features=152, out_features=159, bias=True)
    (6): Linear(in_features=159, out_features=54, bias=True)
    (7): Linear(in_features=54, out_features=39, bias=True)
    (8): Linear(in_features=39, out_features=36, bias=True)
    (9): Linear(in_features=36, out_features=33, bias=True)
    (10): Linear(in_features=33, out_features=1, bias=True)
  )
)
Learningrate Range: [0.0001, 0.0016]
Maximum Epochs: (7, 12)
Chosen Optimizer: Adam
Result Encoding: {5409: {'lr': 0.0001, 'epochen': 7}, 9903: {'lr': 0.0016, 'epochen': 7}, 5471: {'lr': 0.0001, 'epochen': 8}, 7489: {'lr': 0.0016, 'epochen': 8}, 6405: {'lr': 0.0001, 'epochen

/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")


relu sigmoid tanh layer_sum dropout_loc      mae     mae_l      lr  epochs
0     6       0    0         8           2  1.66279  1.228682  0.0016      10
1     8       0    0        10           5  1.66667  1.228682  0.0016       8
2     3       2    0         7           4  1.63566  1.232558  0.0016       7
3     2       2    2         8           4  1.54651  1.201550  0.0001      10
4     3       4    2        11           2  1.65504  1.515504  0.0016      10
5     0       0    6         8           3  1.65116  1.298450  0.0001      11
6     4       2    2        10           5  1.52326  1.205426  0.0001      11
7     0       0    5         7           3  1.64729  1.232558  0.0001      11
8     6       2    0        10           3  1.61628  1.255814  0.0016      10
9     4       1    0         7           2  1.64729  1.310078  0.0016      11
10    2       1    3         8           7  1.59302  1.267442  0.0001      11
11    8       0    0        10           7  1.63953  1.228682  0.0016       9
12    6       0    1         9           2  1.60078  1.251938  0.0016       8
13    6       0    0         8           4  1.64729  1.248062  0.0016      10
14    6       0    0         8           3  1.66279  1.251938  0.0016      11
15    2       0    3         7           3  1.57364  1.240310  0.0016       7
16    1       2    2         7           2  1.64341  1.236434  0.0016      11
17    4       3    1        10           3  1.61628  1.228682  0.0016      10
18    4       1    2         9           2  1.65116  1.484496  0.0001       9
19    0       0    5         7           5  1.55039  1.228682  0.0001      10
20    2       1    2         7           3  1.57364  1.220930  0.0016       7
21    5       2    1        10           2  1.63566  1.228682  0.0016      11
22    7       0    0         9           4  1.63953  1.232558  0.0016       7
23    0       0    6         8           3  1.64341  1.290698  0.0001      10
24    3       1    1         7           3  1.60078  1.224806  0.0016       8
25    4       0    4        10           2  1.66667  1.480620  0.0001      11
26    5       0    0         7           3  1.65891  1.259690  0.0016       9
27    2       1    2         7           5   1.5814  1.236434  0.0016      11
28    7       0    0         9           4  1.63566  1.228682  0.0016      11
29    9       0    0        11           3  1.66279  1.251938  0.0016       9

In [ ]:
auswertung.to_csv("auswertung_netze_lrep.csv",sep = ";")
print(dynamische_netze)

[{'first': ['linear', 52, 154], 'relu5': ['dropout', 154, 194], 'no_activation3': ['linear', 154, 187], 'relu6': ['linear', 187, 198], 'relu7': ['linear', 198, 200], 'relu8': ['linear', 200, 170], 'relu9': ['linear', 170, 163], 'relu10': ['linear', 163, 1], 'epochen': 10, 'lr': 0.0016, 'mae': 1.2286821705426356}, {'first': ['linear', 52, 162], 'relu1': ['linear', 162, 185], 'relu2': ['linear', 185, 191], 'relu3': ['linear', 191, 194], 'relu4': ['dropout', 194, 200], 'no_activation6': ['linear', 194, 197], 'relu6': ['linear', 197, 171], 'relu7': ['linear', 171, 108], 'relu8': ['linear', 108, 40], 'relu9': ['linear', 40, 1], 'epochen': 8, 'lr': 0.0016, 'mae': 1.2286821705426356}, {'first': ['linear', 52, 183], 'relu0': ['linear', 183, 200], 'sigmoid1': ['linear', 200, 200], 'relu2': ['dropout', 200, 200], 'no_activation5': ['linear', 200, 42], 'sigmoid3': ['linear', 42, 30], 'relu4': ['linear', 30, 1], 'epochen': 7, 'lr': 0.0016, 'mae': 1.2325581395348837}, {'first': ['linear', 52, 148],

## Cross Validation
**Ausführungsdauer: ~8h**<br>
Hier werden die optimalen Netze mit Hilfe einer Crossvalidation neu trainiert und dann getestet, um das beste der 30 Netz zu finden.

In [1]:
def cross_validate(netz, dataset,sliced_races,percent = 0.1, cuda = "y"):
    #Festlegen der Lernrate des Netzes. Ausserdem werden die Rennen hier geshuffelt und der upper und lower bound für die 
    #trainingsdaten festgelegt. 
    dict_keys = list(dataset.keys())
    random.shuffle(dict_keys)
    lower = 0
    upper = int(np.round(len(dict_keys)*0.1,0))
    print("Upper:",upper)
    opt = {}
    lr = netz["lr"]
    max_epochs = netz["epochen"]
    for key in netz.keys():
        if key not in ['mae', 'lr', 'epochen']:#mae wird noch in dictionary von HP_Optimizer hinzugefügt und muss entfernt werden
            opt[key] = netz[key]
    model = NetzDynamic(opt)
    
    
    if cuda.lower() == 'y':
        model.cuda() 
    
    
    optimizer = optim.Adam(model.parameters(), lr = lr)     
    
    def train_cuda(epoch):
        model.train()
        batch_id = 0
        for key in train_T.keys():
            
            for data, target in train_T[key]:
                data = data.cuda()
                target = torch.Tensor(target).unsqueeze(0).cuda()
                shape = target.size()[1]
                target = target.resize(shape,1).cuda()
                optimizer.zero_grad()
                out = model(data)
                criterion = nn.MSELoss()
                loss = criterion(out, target)
                loss.backward()
                optimizer.step()
                #print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                #    epoch, batch_id *len(data), len(train),
                #100. * batch_id / len(train), loss.item()))
                batch_id +=1
        print("Epoche:",epoch)
    def train_(epoch):
        model.train()
        batch_id = 0
        for key in train_T.keys():
            for data, target in train_T[key]:
                #data = data.cuda()
                target = torch.Tensor(target).unsqueeze(0)#.cuda()
                shape = target.size()[1]
                target = target.resize(shape,1)#.cuda()
                optimizer.zero_grad()
                out = model(data)
                #print("Out: ", out, out.size())
                #print("Target: ", target, target.size())
                criterion = nn.MSELoss()
                loss = criterion(out, target)
                loss.backward()
                optimizer.step()
                print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                    epoch, batch_id *len(data), len(train),
                100. * batch_id / len(train), loss.item()))
                batch_id +=1
    def test_times_cuda(test_final):
        total = 0
        count = 0
        result_dict = {}
        help_dict = {}
        result = pd.DataFrame(columns = ['target','prediction'])
        for key in test_final.keys():
            help_dict = {}
            for data, target in test_final[key]:
                model.eval()
                data = data.cuda()
                target = torch.Tensor(target).unsqueeze(0)
                shape = target.size()[1]
                target = target.resize(shape,1).cuda()
                out = model(data).cpu()
                out = out.detach().numpy()
                target = target.cpu()
                target = target.detach().numpy()
                total += abs(out - target[0][0])
                help_dict[target[0][0]] = out
                count+=1
        
        
            #Auslesen der predicteten Werte A und der zugehörigen targets y
            A = [x[0][0] for x in list((help_dict.values()))]
            y = list(help_dict.keys())
            
            #Anfügen der Werte an Result
            t = pd.DataFrame()
            t['target'] = y
            t['prediction_value'] = A
            t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
            t.reset_index(inplace = True)
            t.rename(columns = {'index':'prediction'}, inplace = True)
            t['prediction'] = t['prediction']+1
            result = result.append(t, sort = True)
            #print(result)
        return result

    def test_times(test_final):
        total = 0
        count = 0
        result_dict = {}
        help_dict = {}
        result = pd.DataFrame(columns = ['target','prediction'])
        for key in test_final.keys():
            help_dict = {}
            for data, target in test_final[key]:
                model.eval()
                target = torch.Tensor(target).unsqueeze(0)
                shape = target.size()[1]
                target = target.resize(shape,1)
                out = model(data)
                out = out.detach().numpy()
                target = target.detach().numpy()
                total += abs(out - target[0][0])
                help_dict[target[0][0]] = out
                count+=1
            #Auslesen der predicteten Werte A und der zugehörigen targets y
            A = [x[0][0] for x in list((help_dict.values()))]
            y = list(help_dict.keys())
            
            #Anfügen der Werte an Result
            t = pd.DataFrame()
            t['target'] = y
            t['prediction_value'] = A
            t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
            t.reset_index(inplace = True)
            t.rename(columns = {'index':'prediction'}, inplace = True)
            t['prediction'] = t['prediction']+1
            result = result.append(t, sort = True)
            
        return result_dict            
        
    result_dfs = {} 
    counter = 0
    final_result = pd.DataFrame(columns = ['target','prediction'])
    while lower <= len(dict_keys): #Solange unsere Untergrenze noch unter der gesamtanzahl der Keys ist wird trainiert.
        try: #Es wird versucht ob die upper boundary noch in der länge der Key liste ist. Wenn das der Fall ist wird 
            #try ausgeführt. Wenn upper nichtmehr da ist, wird einfach lower bis ende als Test genommen
            test = dict_keys[lower:upper]
            train = [key for key in dict_keys if key not in test]
            train_T = {key:dataset[key] for key in train}
            test_T = {key:dataset[key] for key in test}
        except:
            test = dict_keys[lower:]
            train = [key for key in dict_keys if key not in test]
            train_T = {key:dataset[key] for key in train}
            test_T = {key:dataset[key] for key in test}
        
        if cuda.lower() == 'y': #Netz wird auf der Grafikkarte trainiert
            for epoch in range(1,max_epochs):
                train_cuda(epoch) 
        else:
            for epoch in range(1,max_epochs):
                train_(epoch) 
        
        if cuda.lower() =='y':
            total_results = test_times_cuda(test_T)        
        else:
            total_results = test_times(test_T)
        final_result = final_result.append(total_results)
        lower = upper 
        upper += upper
        
    return final_result


In [ ]:
cross_end = {}
#train dev test split vom anfang wird nicht mehr benötigt
all_data = to_tensor(sliced_races, {},{}, nogo_columns)[0]
for netz_temp in dynamische_netze:
    auswertung = cross_validate(netz_temp, all_data,sliced_races,percent = 0.25, cuda = "y")
    A = auswertung.prediction.tolist()
    Y = auswertung.target.tolist()
    MAE_final = MAE(A,Y)
    cross_end[MAE_final] = netz_temp #Das netz wird mit MAE als key in ein Dictonary gespeichert um zu entscheiden welches
                                     #am Besten performed hat insgesammt. Dieses wird dann auf allen Daten trainiert.

Upper: 14


/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")


Epoche: 1
Epoche: 2
Epoche: 3
Epoche: 4
Epoche: 5
Epoche: 6
Epoche: 7
Epoche: 8
Epoche: 9


/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.

Epoche: 1
Epoche: 2
Epoche: 3
Epoche: 4
Epoche: 5
Epoche: 6
Epoche: 7
Epoche: 8
Epoche: 9


...

/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.

Epoche: 1
Epoche: 2
Epoche: 3
Epoche: 4
Epoche: 5
Epoche: 6
Epoche: 7
Epoche: 8


/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.

Epoche: 1
Epoche: 2
Epoche: 3
Epoche: 4
Epoche: 5
Epoche: 6
Epoche: 7
Epoche: 8


/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")
/usr/local/lib/python3.6/dist-packages/torch/tensor.

**Ausgabe der Ergebnisse der Crossvalidation:**<br>
Für jedes Netz wird noch einmal sein Dictionary (erzeugt mit Hilfe von NetzDynamic Klasse ein Neuronales Netz) und der durch die Crossvalidation berechnete neue MAE. Der neue MAE liegt als Dictionary-Key vor und verweist auf das jeweilige Netz, sodass das Netz mit dem niedrigsten crossvalidation-MAE einfach identifiziert werden kann.

In [ ]:
print(cross_end)

{1.4961538461538462: {'first': ['linear', 52, 154], 'relu5': ['dropout', 154, 194], 'no_activation3': ['linear', 154, 187], 'relu6': ['linear', 187, 198], 'relu7': ['linear', 198, 200], 'relu8': ['linear', 200, 170], 'relu9': ['linear', 170, 163], 'relu10': ['linear', 163, 1], 'epochen': 10, 'lr': 0.0016, 'mae': 1.2286821705426356}, 1.4253846153846155: {'first': ['linear', 52, 162], 'relu1': ['linear', 162, 185], 'relu2': ['linear', 185, 191], 'relu3': ['linear', 191, 194], 'relu4': ['dropout', 194, 200], 'no_activation6': ['linear', 194, 197], 'relu6': ['linear', 197, 171], 'relu7': ['linear', 171, 108], 'relu8': ['linear', 108, 40], 'relu9': ['linear', 40, 1], 'epochen': 8, 'lr': 0.0016, 'mae': 1.2286821705426356}, 1.4938461538461538: {'first': ['linear', 52, 183], 'relu0': ['linear', 183, 200], 'sigmoid1': ['linear', 200, 200], 'relu2': ['dropout', 200, 200], 'no_activation5': ['linear', 200, 42], 'sigmoid3': ['linear', 42, 30], 'relu4': ['linear', 30, 1], 'epochen': 7, 'lr': 0.0016

In [ ]:
min(cross_end.keys())

1.3692307692307693

In [ ]:
print('finales Netz:\n')
print(cross_end[min(cross_end.keys())])

{'first': ['linear', 52, 111], 'tanh1': ['linear', 111, 184], 'tanh2': ['linear', 184, 187], 'tanh3': ['linear', 187, 200], 'tanh4': ['dropout', 200, 110], 'no_activation6': ['linear', 200, 196], 'tanh6': ['linear', 196, 1], 'epochen': 10, 'lr': 0.0001, 'mae': 1.2286821705426356}


## Finales Training und Testing
Training des besten Netzes welches durch Crossvalidation ausgewählt wurde. 
<br>Dieses Netz wird auf allen Rennen außer dem letzten Rennen aus der Saison 2017 trainiert. Diese Saison ist die letzte zur Verfügung stehende Saison aus dem kaggle Datensatz. Auf diesem Rennen (mit dem key 988) soll das Netz dann final getestet werden.

Ist gibt zwei Möglichkeiten diesen Tets auszuführen:
<br>**1. Möglichkeit:**<br>
Das komplette Jupyter Notebook ist bis zu diesem Punkt geladen worden. Dann können die folgenden Zellen einfach bis zu dem Punkt 'Laden eines vortrainierten Modells' ausgeführt werden.

**2. Möglichkeit:**<br>
Es wird das im Zuge dieses Projekts vortrainierte Modell von Github verwendet (Final_F1.pt). Dann müssen die kommenden Zellen übersprungen werden und es kann stattdessen der Code ab 'Laden eines vortrainierten Modells' ausgeführt werden.

In [ ]:
test_T = {}
train_T = {}
test_T[988] = all_data[988]
train_list = list(all_data.keys())
train_T = {key:all_data[key] for key in train_list if key != 988}

In [ ]:
final_netz = {'first': ['linear', 52, 111], 'tanh1': ['linear', 111, 184], 'tanh2': ['linear', 184, 187], 'tanh3': ['linear', 187, 200], 'tanh4': ['dropout', 200, 110], 'no_activation6': ['linear', 200, 196], 'tanh6': ['linear', 196, 1], 'epochen': 10, 'lr': 0.0001, 'mae': 1.2286821705426356}

In [ ]:
def final_training(train_T, test_T, netz, cuda = 'y'):
    opt = {}
    lr = netz["lr"]
    max_epochs = netz["epochen"]
    for key in netz.keys():
        if key not in ['mae', 'lr', 'epochen']:#mae wird noch in dictionary von HP_Optimizer hinzugefügt und muss entfernt werden
            opt[key] = netz[key]
    model = NetzDynamic(opt)
  
  
    if cuda.lower() == 'y':
          model.cuda() 
    
    optimizer = optim.Adam(model.parameters(), lr = lr)     
      
    def train_cuda(epoch):
        model.train()
        batch_id = 0
        for key in train_T.keys():
            
            for data, target in train_T[key]:
                data = data.cuda()
                target = torch.Tensor(target).unsqueeze(0).cuda()
                shape = target.size()[1]
                target = target.resize(shape,1).cuda()
                optimizer.zero_grad()
                out = model(data)
                criterion = nn.MSELoss()
                loss = criterion(out, target)
                loss.backward()
                optimizer.step()
                  #print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                  #    epoch, batch_id *len(data), len(train),
                  #100. * batch_id / len(train), loss.item()))
                batch_id +=1
        print("Epoche:",epoch)
        
    def train_(epoch):
        model.train()
        batch_id = 0
        for key in train_T.keys():
            for data, target in train_T[key]:
                #data = data.cuda()
                target = torch.Tensor(target).unsqueeze(0)#.cuda()
                shape = target.size()[1]
                target = target.resize(shape,1)#.cuda()
                optimizer.zero_grad()
                out = model(data)
                #print("Out: ", out, out.size())
                #print("Target: ", target, target.size())
                criterion = nn.MSELoss()
                loss = criterion(out, target)
                loss.backward()
                optimizer.step()
                print("Train Epoche: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}".format(
                    epoch, batch_id *len(data), len(train),
                100. * batch_id / len(train), loss.item()))
                batch_id +=1
    def test_times_cuda(test_final):
        total = 0
        count = 0
        result_dict = {}
        help_dict = {}
        result = pd.DataFrame(columns = ['target','prediction'])
        for key in test_final.keys():
            help_dict = {}
            for data, target in test_final[key]:
                model.eval()
                data = data.cuda()
                target = torch.Tensor(target).unsqueeze(0)
                shape = target.size()[1]
                target = target.resize(shape,1).cuda()
                out = model(data).cpu()
                out = out.detach().numpy()
                target = target.cpu()
                target = target.detach().numpy()
                total += abs(out - target[0][0])
                help_dict[target[0][0]] = out
                count+=1
          
          
            #Auslesen der predicteten Werte A und der zugehörigen targets y
            A = [x[0][0] for x in list((help_dict.values()))]
            y = list(help_dict.keys())
            
            #Anfügen der Werte an Result
            t = pd.DataFrame()
            t['target'] = y
            t['prediction_value'] = A
            t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
            t.reset_index(inplace = True)
            t.rename(columns = {'index':'prediction'}, inplace = True)
            t['prediction'] = t['prediction']+1
            result = result.append(t, sort = True)
            #print(result)
        return result
  
    def test_times(test_final):
        total = 0
        count = 0
        result_dict = {}
        help_dict = {}
        for key in test_final.keys():
            help_dict = {}
            for data, target in test_final[key]:
                model.eval()
                target = torch.Tensor(target).unsqueeze(0)
                shape = target.size()[1]
                target = target.resize(shape,1)
                out = model(data)
                out = out.detach().numpy()
                target = target.detach().numpy()
                total += abs(out - target[0][0])
                help_dict[target[0][0]] = out
                count+=1
            #Auslesen der predicteten Werte A und der zugehörigen targets y
            A = [x[0][0] for x in list((help_dict.values()))]
            y = list(help_dict.keys())
            
            #Anfügen der Werte an Result
            t = pd.DataFrame()
            t['target'] = y
            t['prediction_value'] = A
            t = sqldf.sqldf('''select * from t order by prediction_value ASC''')
            t.reset_index(inplace = True)
            t.rename(columns = {'index':'prediction'}, inplace = True)
            t['prediction'] = t['prediction']+1
            result = result.append(t, sort = True)
            
        return result_dict  
  
    if cuda.lower() == 'y': #Netz wird auf der Grafikkarte trainiert
        for epoch in range(1,max_epochs):
            train_cuda(epoch) 
    else:
        for epoch in range(1,max_epochs):
            train_(epoch) 
          
    if cuda.lower() =='y':
        total_results = test_times_cuda(test_T)        
    else:
        total_results = test_times(test_T)
    #torch.save(model, "Final_F1_2.pt")
    #files.download("Final_F1.pt")
    return total_results

In [ ]:
final_netz = cross_end[min(cross_end.keys())]
if cuda.lower() == 'y':
    final_output = final_training(train_T, test_T, final_netz, cuda = 'y')
else:
    final_output = final_training(train_T, test_T, final_netz, cuda = 'n')

/usr/local/lib/python3.6/dist-packages/torch/tensor.py:365: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")


Epoche: 1
Epoche: 2
Epoche: 3
Epoche: 4
Epoche: 5
Epoche: 6
Epoche: 7
Epoche: 8
Epoche: 9


/usr/local/lib/python3.6/dist-packages/torch/serialization.py:402: UserWarning: Couldn't retrieve source code for container of type NetzDynamic. It won't be checked for correctness upon loading.
  "type " + obj.__name__ + ". It won't be checked "


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
final_output

prediction  prediction_value  target
0           1          2.941729     1.0
1           2          3.514159     2.0
2           3          4.024145     3.0
3           4          4.978887     4.0
4           5          5.539691     5.0
5           6          8.209292     8.0
6           7          9.617919     7.0
7           8          9.890086     6.0
8           9         11.608427     9.0
9          10         12.027296    10.0
10         11         12.225893    11.0
11         12         14.294198    14.0
12         13         14.500388    16.0
13         14         14.518767    18.0
14         15         14.901320    12.0
15         16         15.369975    17.0
16         17         15.688929    13.0
17         18         16.746038    15.0
18         19         20.045355    20.0

In [ ]:
def test_times_cuda(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        help_dict = {}
        for data, target in test_final[key]:
            model.eval()
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            out = model(data).cpu()
            out = out.detach().numpy()
            target = target.cpu()
            target = target.detach().numpy()
            total += abs(out - target[0][0])
            help_dict[target[0][0]] = out
            count+=1
        result_dict[key] = help_dict
        
    return result_dict

def test_times(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        help_dict = {}
        for data, target in test_final[key]:
            model.eval()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1)
            out = model(data)
            out = out.detach().numpy()
            target = target.detach().numpy()
            total += abs(out - target[0][0])
            help_dict[target[0][0]] = out
            count+=1
        result_dict[key] = help_dict
        
    return result_dict

if cuda.lower() =='y':
    total_results = test_times_cuda(test_T)
else:
    total_results = test_times(test_T)

#### Laden eines vortrainierten Modells:
**Ausführungsdauer: ~4 Minuten**<br>
Falls die enstprechenden Zellen zuvor nicht ausgeführt wurden, werden die essenziell benötigten Funktionen und Klassen hier nocheinmal bereitgestellt:

In [4]:
def test_times_cuda(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        help_dict = {}
        for data, target in test_final[key]:
            model.eval()
            data = data.cuda()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1).cuda()
            out = model(data).cpu()
            out = out.detach().numpy()
            target = target.cpu()
            target = target.detach().numpy()
            total += abs(out - target[0][0])
            help_dict[target[0][0]] = out
            count+=1
        result_dict[key] = help_dict
        
    return result_dict

def test_times(test_final):
    total = 0
    count = 0
    result_dict = {}
    help_dict = {}
    for key in test_final.keys():
        help_dict = {}
        for data, target in test_final[key]:
            model.eval()
            target = torch.Tensor(target).unsqueeze(0)
            shape = target.size()[1]
            target = target.resize(shape,1)
            out = model(data)
            out = out.detach().numpy()
            target = target.detach().numpy()
            total += abs(out - target[0][0])
            help_dict[target[0][0]] = out
            count+=1
        result_dict[key] = help_dict
        
    return result_dict

def load_data(directory = 'sliced_data'):
    '''
        Funktion, die die aufbereiteten/vorbereiteten Daten aus existierenden CSV Dateien 
        einliest und je nach Vollständigkeit in zwei Dictionaries abspeichert,
        geschlüsselt nach der jeweiligen RaceId
    '''
    if os.path.exists(directory):
        csv_filenames = []
        #auslesen aller csv file dateinamen aus formula 1 datensatz und abspeichern in liste
        for filename in os.listdir(os.getcwd()+'/'+directory):
            typ = filename.split('.')[-1]
            name = filename.split('.')[0]
            if typ == 'csv':
                csv_filenames.append(filename)
        sliced_races = {}
        #einlesen und abspeichern als dataframe aller dateien
        for file in csv_filenames:
            try:
                df = pd.read_csv(directory+'/'+file, engine = 'python', sep = ';', decimal = '.')
                del df['Unnamed: 0']
            except Exception as e:
                df = pd.read_csv(directory+'/'+file, engine = 'c', sep = ';', decimal = '.')
                del df['Unnamed: 0']
                print(e)
            f = int(file.split('_')[-1].split('.')[0]) #raceid wird als key gesetzt
            sliced_races[f] = df
        print('Einlesen der '+directory+' Dateien erfolgreich')
    else:
        raise ('sliced Dateien können nicht eingelesen werden, da kein entsprechendes Verzeichnis existiert!')
   
    return sliced_races

def to_tensor(train_data, dev_data, test_data, nogo_columns = []):
    '''
        Funktion erhält zuvor erzeugte train, dev und test Dictionarys mit Formel 1 Rennen
        und wandelt die DateFrames in Tensoren um. Den Tensoren wird jeweils ihr Target Value
        (podium_podition) zugeordnet. In Dictionary Form werden die Tensoren zurück gegeben.
        Nicht gewollte Spalten (in nogo_columns) werden entfernt.
    '''
    train = []
    train_ = {}
    dev = []
    dev_ = {}
    test = []
    test_ = {}
    
    for id, race in train_data.items():
        for did in race.driverId.unique():
            temp = race.where(race.driverId == did).dropna(how = "all")
            temp_y = list(temp["podium_position"])
            #nicht gewollte Attribute werden aus Datensatz entfernt (bspw. podium_position)
            cols = [col for col in temp.columns if col not in nogo_columns]
            temp_x = temp[cols]
            #die letze runde eines Fahrers wird betrachtet (enthält kumulierte Informationen über zuvor gefahrene Runden)
            temp_x = temp_x.tail(1)
            x_tensor = torch.tensor(temp_x[cols].values)
            train.append((x_tensor, [temp_y[0]]))#speichern von tensor und target als tupel
        train_[id] = train
        train = []
    if len(list(dev_data.keys())) != 0:#wird nur bei train/dev/test benötigt nicht bei train/test
        for id, race in dev_data.items():
            for did in race.driverId.unique():
                temp = race.where(race.driverId == did).dropna(how = "all")
                temp_y = list(temp["podium_position"])
                cols = [col for col in temp.columns if col not in nogo_columns]
                temp_x = temp[cols]
                temp_x = temp_x.tail(1)
                x_tensor = torch.tensor(temp_x[temp_x.columns].values)
                dev.append((x_tensor, [temp_y[0]]))
            dev_[id] = dev
            dev = []
    if len(list(test_data.keys()))!=0:
        for id, race in test_data.items():
            for did in race.driverId.unique():
                temp = race.where(race.driverId == did).dropna(how = "all")
                temp_y = list(temp["podium_position"])
                cols = [col for col in temp.columns if col not in nogo_columns]
                temp_x = temp[cols]
                temp_x = temp_x.tail(1)
                x_tensor = torch.tensor(temp_x[temp_x.columns].values)
                test.append((x_tensor, [temp_y[0]]))
            test_[id] = test
            test = []
        
    return train_,dev_,test_

class NetzDynamic(nn.Module):
    
    def __init__(self, layer_information):
        super(NetzDynamic,self).__init__()
        self.__layer_information = layer_information
        #definieren von einer Moduleliste, die alle Layer des Netzes enthalten wird
        self.layers = nn.ModuleList()
        
        #erzeugen der in layer_information übergebeben Layer und hinzufügen zu layers Moduleliste
        for specs in self.__layer_information.values():
            type_ = specs[0]
            in_ = specs[1]
            out_ = specs[2]
            if type_ == 'linear':
                self.layers.append(nn.Linear(in_,out_))
            if type_ == 'dropout':
                self.layers.append(nn.Dropout())
        
    def forward(self, x):
        #definieren eines dynamischen forward pass, activation function richtet sich nach dictionary key
        lay_idx = 0
        for activation, specs in self.__layer_information.items():
            if activation.startswith('relu'):
                layer = self.layers[lay_idx] #auswählen des relevanten Layers aus layers ModuleList
                if specs[0] == 'dropout':
                    x = F.relu(x.float())#anwenden der activation function
                    x = layer(x)
                else:
                    x = F.relu(x.float())
                    x = layer(x.float()) 
            if activation.startswith('sigmoid'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = torch.sigmoid(x.float())
                    x = layer(x)
                else:
                    x = torch.sigmoid(x.float())
                    x = layer(x.float())
                    
            if activation.startswith('tanh'):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = torch.tanh(x.float())
                    x = layer(x)
                else:
                    x = torch.tanh(x.float())
                    x = layer(x.float())
            if activation.startswith("first"):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float())
            if activation.startswith("no_activation"):
                layer = self.layers[lay_idx]
                if specs[0] == 'dropout':
                    x = layer(x)
                else:
                    x = layer(x.float()) 
            lay_idx += 1#updaten der layerid, um forward pass ins nächste layer zu machen
        
        return x

In [5]:
#laden der Daten, entweder google colab spezifisch oder für ein lokales Notebook
colab = input('Are you using google colab?[y/n]:')
if colab.lower() == 'y':
    from google.colab import files
    cuda = input('Cuda? [y/n]: ')#definieren ob cuda verwendet wird
    uploaded = files.upload()
    
    sliced_races = {}
    for element in uploaded:
        try:
                    df = pd.read_csv(element, engine = 'python', sep = ';', decimal = '.')
                    del df['Unnamed: 0']
        except Exception as e:
                    df = pd.readcsv(element, engine = 'c', sep = ';', decimal = '.')
                    del df['Unnamed: 0']
                    print(e)
        f = int(element.split('_')[-1].split('.')[0]) #raceid wird als key gesetzt
        sliced_races[f] = df
else:
    cuda = input('Cuda? [y/n]: ')#definieren ob cuda verwendet wird
    sliced_races = load_data(directory = 'sliced_data')

#definieren nicht gewollter Attribute (Attribute die nicht dem Modell übergeben werden sollen):
nogo_columns = ['year', 
                'podium_position', 
                'raceId',
                'lap_number',
                'driverId', 
                'driver_fullname',
                'total_milliseconds',
               'lap_in_milliseconds',
               'total_minutes'
                ]
#train dev test split vom anfang wird nicht mehr benötigt
all_data = to_tensor(sliced_races, {},{}, nogo_columns)[0]
test_T = {}
train_T = {}
test_T[988] = all_data[988]
train_list = list(all_data.keys())
train_T = {key:all_data[key] for key in train_list if key != 988}

if cuda.lower() == 'y':
    model = torch.load("Final_F1.pt")
    total_results = test_times_cuda(test_T)
else:
    model = torch.load("Final_F1.pt", map_location=torch.device('cpu'))
    total_results = test_times(test_T)

Are you using google colab?[y/n]:n
Cuda? [y/n]: n
Einlesen der sliced_data Dateien erfolgreich


c:\users\hwebe\appdata\local\programs\python\python37\lib\site-packages\torch\tensor.py:362: UserWarning: non-inplace resize is deprecated
  warnings.warn("non-inplace resize is deprecated")


In [6]:
model

NetzDynamic(
  (layers): ModuleList(
    (0): Linear(in_features=52, out_features=111, bias=True)
    (1): Linear(in_features=111, out_features=184, bias=True)
    (2): Linear(in_features=184, out_features=187, bias=True)
    (3): Linear(in_features=187, out_features=200, bias=True)
    (4): Dropout(p=0.5, inplace=False)
    (5): Linear(in_features=200, out_features=196, bias=True)
    (6): Linear(in_features=196, out_features=1, bias=True)
  )
)

In [7]:
result_dfs = {}
for raceId, dict in total_results.items():    
    #Auswerten der Vorhersagen aus den Outputdaten des Modells
    A = [x[0][0] for x in list((dict.values()))]
    y = list(dict.keys())
    t = pd.DataFrame(columns = ['target', 'prediction'])
    t['target'] = y
    t['prediction'] = A
    #print("raceId", raceId)
    temp = sliced_races[raceId]
    #name = split_by_race[raceId].where()
    #sortieren des DataFrames nach den vorhergesagten Positionen, aufsteigend
    end = sqldf.sqldf('''select * from t order by prediction ASC''')
    end.reset_index(inplace = True)
    #Da DF nun nach prediction aufsteigend sortiert ist, kann veränderter Index als predictete Position gesetzt werden
    end.rename(columns = {'index': 'predicted_position'},inplace = True)
    #zur Übersichtlichkeit wird nun der endgültige DF nach den richtigen Positionen (target) sortiert (aufsteigend)
    end = sqldf.sqldf('''select * from end order by target ASC''')
    end['predicted_position'] = end['predicted_position']+1
    pred_name = sqldf.sqldf("""select 
                distinct
                d.driver_fullname as name,
                t.predicted_position as pred,
                d.podium_position as target_position
                from 
                end t inner join temp d
                on t.predicted_position = d.podium_position""")
    end["driver_pred"] = 0
    end["driver_target"] = 0
    for pos in temp.podium_position.unique():
        
        name = temp.where(temp.podium_position == pos).dropna(how = "all")
        #print(name)
        name_ = name["driver_fullname"][list(name.index)[0]]
        idx_target = end.where(end.target == pos).dropna(how = "all").index
        idx_pred = end.where(end.predicted_position == pos).dropna(how = "all").index
        end.loc[idx_target,"driver_target"] = name_
        end.loc[idx_pred,"driver_pred"] = name_
        
    #umstellen der Spaltenreihenfolge
    '''end = end[['target', 'predicted_position', 'prediction',"driver_target", "driver_pred"]]
    end_dyn = end_dyn[['target', 'predicted_position', 'prediction',"driver_target", "driver_pred"]]'''
    end = end[['target', 'predicted_position', 'prediction', 'driver_pred', 'driver_target']]
    result_dfs[raceId] = end
    
result_dfs[988].head(10)

target  predicted_position  prediction          driver_pred  \
0     1.0                   1    2.941729      Valtteri Bottas   
1     2.0                   2    3.514159       Lewis Hamilton   
2     3.0                   3    4.024145     Sebastian Vettel   
3     4.0                   4    4.978886  Kimi RÃŒ_ikkÃŒÂ¦nen   
4     5.0                   5    5.539690       Max Verstappen   
5     6.0                   8    9.890086         Esteban Ocon   
6     7.0                   7    9.617919      Sergio PÃŒÂ©rez   
7     8.0                   6    8.209293    Nico HÃŒ_lkenberg   
8     9.0                   9   11.608426      Fernando Alonso   
9    10.0                  10   12.027296         Felipe Massa   

         driver_target  
0      Valtteri Bottas  
1       Lewis Hamilton  
2     Sebastian Vettel  
3  Kimi RÃŒ_ikkÃŒÂ¦nen  
4       Max Verstappen  
5    Nico HÃŒ_lkenberg  
6      Sergio PÃŒÂ©rez  
7         Esteban Ocon  
8      Fernando Alonso  
9         Felipe Massa